# esta función recoge las posibilidades de incendio en un area de white wolf del parke de yosemite: (-119.641, 37.869) 

Se quiere hacer un  devolver un heatmap de 10km de lado. por lo que para hacer la convolucion de cada esquina, habrá que anayadir 6km a cada esquina. por lo tanto los datos de entrada tendran que ser de 22k de lado. 

para evitar posibles errores en la rotacion de la recogida del "quadrado" de recogida, creamos primero un tif con 30km de lado con el punto central deseado. Esto evitara tener que cargar los tifs completos al inicio de la creacion de cada matriz. 




idealmente podriamos mirar los datos metereologicos de un dia antes del llamado RIM FIRE del 17 de agostos de 2013 que resulto en el incendio de 255 acres... para ver que hubiera predicho nuestra prediccion. 

de momento, usaremos los datos del 13 de Noviembre de 2010 (wrf_LT_d03_2010-11-13.nc)


la proyeccion del mapa representara la distancia elegida + 500m por banda (250m x lado)

# LA FUNCION 
creacionPuntosHeatMap(long=-119.641,lat=37.869,tamanyoLadoMapaMetros=10000,precisionX10KmDeLado=20)

DEVUELVE:
    - UN LISTADO DE PUNTOS QUE FORMARAN EL MAPA
    - LOS 4 EXTREMOS QUE DELIMITAN EL AREA NECESARIA PARA HACER LA CONVOLUCIONAL DE CADA PUNTO
    
 hay que ajustar la parte de 
     -Seleccion de tif: para quese pueda elegir cualqueir punto del mapa (quizas creando tifs generales o asegurando que los trozos de tifs originales estan superpuestos. Ahora estan preparados para recoger areas de 13.5km pero deberian poder recoger zonas de 22km de lado.
     
     

In [1]:


import numpy as np
import pandas as pd
import geopandas as gpd

import rasterio 
from rasterio.mask import mask
from rasterio import plot

from pyproj import Proj, transform
from shapely.geometry import Point,Polygon


from PIL import Image
import matplotlib.pyplot as plt

import csv 
import fiona
import pickle

import datetime
import time


from collections import Counter

import shapely.geometry
from shapely.geometry import Polygon
from shapely.ops import cascaded_union
from netCDF4 import Dataset

import os

from tensorflow import keras
#%matplotlib inline


import matplotlib.pyplot as plt
import numpy as np



# 1. FUNCIONES GENERALES DE CREACION DE PUNTOS

In [2]:
#FUNCIONES GENEERALES DE CREACION DE PUNTOS


#este ultimo podria abarcar los anteriores. PENDIENTE
def GeoPointsTranslator(x,y,deESPG=4326,aESPG=5070): #42303
    #USAMOS ESTA PROYECCION PQ PARECE ADECUADA PARA CALIFORNIA PERO PARECE QUE TB PODRIA SER  ESPG:42303

    inProj = Proj("+init=EPSG:"+str(deESPG),preserve_units=True)    
    outProj  = Proj("+init=EPSG:"+str(aESPG))#,preserve_units=True)
 
    return transform(inProj,outProj,x,y)



def creacionPuntosHeatMap(long=-119.641,lat=37.869,tamanyoLadoMapaMetros=10000,precisionX10KmDeLado=20):

    #transformamos las coordenadas a metros
    xc,yc=GeoPointsTranslator(long,lat,deESPG=4326,aESPG=5070)

    #puntos hay por lado del mapa
    distanciaEntrePuntos= tamanyoLadoMapaMetros/precisionX10KmDeLado
    if distanciaEntrePuntos < 500:
        print(f"La distancia minima es de 500m entre punto y punto.")
        return
    else:
        print(f'Se recoge un punto cada {distanciaEntrePuntos} metros')


    #buscamos los extremos de x e y (esto da 2 puntos long lat)
    xc0=xc-(tamanyoLadoMapaMetros/2)
    xc1=xc+(tamanyoLadoMapaMetros/2)
    yc0=yc-(tamanyoLadoMapaMetros/2)
    yc1=yc+(tamanyoLadoMapaMetros/2)

    if precisionX10KmDeLado<2:
        
        print(f"Toda el area del mapa solo cuenta con un punto de medicion es {long,lat}")
        punto= (long,lat)
        return punto

    else:
        coord_Long=[]
        coord_Lat=[]

        # si solo queremos 2 puntos ya los tenemos ya los tenemos.
        # si queremos 3 hay que dividir el espacio en 2 y quedan los extremos y el punto central (=3)
        distanciaEntrePuntosX=(xc1-xc0)/(precisionX10KmDeLado-1)
        distanciaEntrePuntosY=(yc1-yc0)/(precisionX10KmDeLado-1)
        
        
    #CREACION DE UN DF CON TODOS LAS COORDENADAS DELOS X PUNTOS EN ESPG 4326
        
        #los puntos iniciales xc0 y yc0 ESTAN EN METROS, EN ESPG=5070)
        puntoX=xc0
        puntoY=yc0
        
        # xf,yf los pasamos a coordendas 4326 estos son los puntos iniciales del df
        xf,yf=GeoPointsTranslator(puntoX,puntoY,deESPG=5070,aESPG=4326)
        coord_Long.append(xf)
        coord_Lat.append(yf)

        #vamos sumando partes y anyadiendo partes hasta que llegamos al final xc1 y yc1
        while puntoX<xc1:
            
            puntoX=puntoX+distanciaEntrePuntosX
            puntoY=puntoY+distanciaEntrePuntosY
            
            
            #para anadirlos al df los guradamos como coordendas 4326
            xf,yf=GeoPointsTranslator(puntoX,puntoY,deESPG=5070,aESPG=4326)            
            coord_Long.append(xf)
            coord_Lat.append(yf)  

        listaDePuntos=[]
        
        for longitud in range(len(coord_Long)):
            for latitud in range(len(coord_Lat)):
                coordenadas=(coord_Long[longitud],coord_Lat[latitud])
                listaDePuntos.append(coordenadas)
                

        #print(f'Las esquinas del mapa son:\n{mx0,my0,mx1,my1}')
        print(f'EL MAPA SE BASARA EN {len(listaDePuntos)} PUNTOS DE INFORMACION\n')
        print(f'Las esquinas del mapa son:\n{listaDePuntos[0],listaDePuntos[(precisionX10KmDeLado-1)],  listaDePuntos[-precisionX10KmDeLado],listaDePuntos[-1]}')

        
        #creamos un df con los puntos y la fecha del netcdf 
        longT=[]
        latT=[]
        x0=[]
        x1=[]
        y0=[]
        y1=[]
        for x in range(len(listaDePuntos)):
            longT.append(listaDePuntos[x][0])
            latT.append(listaDePuntos[x][1])

        df = pd.DataFrame()
        df['long']=longT
        df['lat']=latT
        df['datos']='Sin datos'        
        
        
        
        
        
    #RECOPILACION DE LOS PUNTOS DONDE CORTAR EL TIF DE DATOS TOPOGRAFICOS EN METROS ESPG5070
        
        # el buffer es el espacio extra (fuera del mapa resultante) que debemos recoger para poder hacer una convolucional.
        # teoricamente deberia bastar con 6km por lado, pero para asegurarnos de que no se pierde informacion por la rotacion de la proyeccion recogemos 7km x lado
        
        bufferXc0=xc0-7000
        bufferYc0=yc0-7000
        bufferXc1=xc1+7000
        bufferYc1=yc1+7000
        
        esquinasTif=[bufferXc0,bufferYc0,bufferXc1,bufferYc1]
        
    return(df, esquinasTif)

#df, esquinasTif=creacionPuntosHeatMap(-119.77, 37.85,tamanyoLadoMapaMetros=10000,precisionX10KmDeLado=3)
#print(esquinasTif)
#df

# 2. FUNCIONES PARA RECOLECCION DE TOPOGRAFIA

In [3]:
# 2. FUNCIONES PARA TOPOGRAFIA

#Seleccion de tif


def seleccionTifDEM(long,lat):

    if (lat > 38.9):
        
        tifEntreComillas="LF/DEMTIFS/dem_1.tif"  

    elif (lat > 35.8):
        
        tifEntreComillas="LF/DEMTIFS/dem_2_3_4.tif"   
        
    elif (long < -119.1):

        tifEntreComillas="LF/DEMTIFS/dem_2_3_4.tif"      
        
    elif (lat > 35.2) and (long < -118): 

        tifEntreComillas="LF/DEMTIFS/dem_2_3_4.tif"       

    else:    
        
        tifEntreComillas="LF/DEMTIFS/dem_5.tif"  
 
    return tifEntreComillas


def seleccionTifSlope(long,lat):

    if (lat > 37.5) and (long < -119.5):
        
        tifEntreComillas="LF/SlopeTIFS/slope_1.tif"  
        
    else:    
        
        tifEntreComillas="LF/SlopeTIFS/slope_2_3_4.tif"  
 
    return tifEntreComillas


def seleccionTifASPECT(long,lat):

    if (long < -119.5):
        
        tifEntreComillas="LF/AspectTIFS/aspect_1_2_3.tif"  
       
    else: 
        
        tifEntreComillas="LF/AspectTIFS/aspect_2_4.tif" 
 
    return tifEntreComillas


def seleccionTifFuel(long,lat):

    if (long < -118):
        
        tifEntreComillas="LF/fuel_13/fuel_1.tif"  
       
    else: 
        
        tifEntreComillas="LF/fuel_13/fuel_2.tif" 
 
    return tifEntreComillas




def estaDentroTIF(long,lat,boundary):
    estaDentro=True
    df = pd.DataFrame([[long,lat]], columns=list('XY'))
    punto= gpd.GeoDataFrame(df, geometry=gpd.points_from_xy(df['X'], df['Y']))
    punto.crs={'init': 'epsg:4326'}

    if punto.within(boundary)[0]==False:
        print('No tenemos datos de este punto geografico')
        estaDentro=False
    return estaDentro



#esta funcion crea los tifs que necesitamos para recorrer el terreno deseado todos los resultados de topografia en 

def tifAnalisis(longWGS,latWGS,esquinasTif, boundary):
    
    extremoX0,extremoY0,extremoX1,extremoY1=esquinasTif

    extremo00=extremoX0,extremoY0
    extremo10=extremoX1,extremoY0
    extremo11=extremoX1,extremoY1
    extremo01=extremoX0,extremoY1

    if estaDentroTIF(longWGS,latWGS,boundary)==False:
        print('No tenemos informacion')
        #return -9999   


        #CAMBIANDO LOS TIFS PODEMOS RECIBIR LAS MATRICES DE OTRAS FUNCIONES
        #Esto depende de los tifs. En este caso son los tifs de SLOPE
    demTif=seleccionTifDEM(longWGS,latWGS)
    sloTif=seleccionTifSlope(longWGS,latWGS)
    aspTif=seleccionTifASPECT(longWGS,latWGS)
    fueTif=seleccionTifFuel(longWGS,latWGS)

    

    extremo00=(extremo00[0],extremo00[1])
    extremo01=(extremo01[0],extremo01[1])
    extremo10=(extremo10[0],extremo10[1])
    extremo11=(extremo11[0],extremo11[1])

    df = gpd.GeoDataFrame([['box', Point(extremo00)],
                            ['box', Point(extremo10)], 
                            ['box', Point(extremo11)], 
                            ['box', Point(extremo01)]],  
                         columns = ['shape_id', 'geometry'], 
                         geometry='geometry')
    #print(df)
    df['geometry'] = df['geometry'].apply(lambda x: x.coords[0])

    df = df.groupby('shape_id')['geometry'].apply(lambda x: Polygon(x.tolist())).reset_index()

        # Declare the result as a new a GeoDataFrame
    poligonoDerecogida = gpd.GeoDataFrame(df, geometry = 'geometry')


    atributos=[demTif,sloTif,aspTif,fueTif] 
    trozos=[]

    nombre=['demTif','sloTif','aspTif','fueTif']
    contador=0
    for tifEntreComillas in atributos: 


        txt=tifEntreComillas[-10:-4]

        tiiif = rasterio.open(tifEntreComillas)

        poligonoDerecogida.crs=tiiif.crs

        poligonoDerecogida.to_file("poligonoDerecogida/poligonoDerecogida.shp")


        #para silenciar
        #poligonoDerecogida.plot()

        with fiona.open("poligonoDerecogida/poligonoDerecogida.shp", "r") as shapefile:
            shapes = [feature["geometry"] for feature in shapefile]


        with rasterio.open(tifEntreComillas) as src:
            out_image, out_transform = rasterio.mask.mask(src, shapes, crop=True)
            out_meta = src.meta

            out_meta.update({"driver": "GTiff",
                             "height": out_image.shape[1],
                             "width": out_image.shape[2],
                             "transform": out_transform})

        with rasterio.open("recortes/"+nombre[contador]+'.tif', "w", **out_meta) as dest:
            dest.write(out_image)

        ros= rasterio.open("recorte.tif")
        contador+=1
        
# FUNCION PARA CONVERTIR LOS DATOS RECOGIDOS DE UN TIF EN UNA MATRIZ PARA CNN

def prepararMatrix(CapaMatriz, ValorMinimoPosible=-999,ValorMaximoPosible=-999, numeroPixels=25, normalizada=True):
   
    #pasamos el array a 1 dimension para poder cambiar Todos los datos extremos por el valor maximo
    a1D = CapaMatriz.reshape((len(CapaMatriz)*len(CapaMatriz[0])),1)

    #creamos un contador de extremos (si hubiera muchos, posiblemente habria un problema con el supuesto valor maximo)
    contadorExtremos0 = 0
    if ValorMinimoPosible != -999:
        for valor in range(len(a1D)):
            if a1D[valor] < ValorMinimoPosible:
                a1D[valor] = ValorMinimoPosible

                contadorExtremos0 = contadorExtremos0+1
       
        #print(f"Se han encontrado {contadorExtremos0} elementos extremos que se han substituido por el valor minimo: {ValorMinimoPosible}")       
        if contadorExtremos0>2:
            print(f"Se han encontrado {contadorExtremos0} elementos extremos que se han substituido por el valor minimo: {ValorMinimoPosible}")       

    else:
        #Si estos valores no estuvieran saldrá un aviso
        ValorMinimoPosible=0
        print("falta el valor minimo posible de este atributo")

 
    contadorExtremos = 0

    if ValorMaximoPosible != -999:
        for valor in range(len(a1D)):
            if a1D[valor] > ValorMaximoPosible:
                a1D[valor] = ValorMaximoPosible
                contadorExtremos = contadorExtremos+1

        #print(f"Se han encontrado {contadorExtremos} elementos extremos que se han substituido por el valor maximo: {ValorMaximoPosible}")       
        if contadorExtremos0>2:
            print(print(f"Se han encontrado {contadorExtremos0} elementos extremos que se han substituido por el valor minimo: {ValorMinimoPosible}"))       
                  
    else:
        #Si estos valores no estuvieran saldrá un aviso
        ValorMaximoPosible=50
        print("falta el valor maximo posible de este atributo")
        
        

    try:

        #devolvemos el array a la matriz original SIN LOS VALORES EXTREMOS
        XArray = a1D.reshape(len(CapaMatriz),len(CapaMatriz[0]))
    #print(f"Sin extremos:\n{XArray}")

        #guardamos los max y minimos de la matriz original
        miniMat=XArray.min()
        maxiMat=XArray.max()
    #print(miniMat)

        XArrayA0 = (XArray-XArray.min()) #esto mueve el rango de 0 a max
        arrayNorm0_1 = XArrayA0/XArrayA0.max() #esto lo normaliza
    #print(f"Normalizada:{arrayNorm0_1}") #Esto es con lo que alimentaremos la imagen para la creacion o fusion de N pixels


        #convertimos el array en una imagen con valor min = 0 azul y max = 255 amarillo
        img = Image.fromarray((arrayNorm0_1 * 255).astype(np.uint8))
    #plt.matshow(img)
        #convertimos la imagen en matriz
        img2 = img.resize((numeroPixels, numeroPixels), Image.BICUBIC) #ANTIALIAS) #BILINEAR) NEAREST

        arrayImagen = np.array(img2, copy=True)

        #print(f"Nuevo Tamanyo:\n{arrayImagen}")

        # CONVERSION DE LA IMAGEN EN COLOR MODIFICADA O NO, A UNA MATRIZ EN BASE A LOS MAXIMOS Y MINIMOS DE LA MATRIZ ORIGINAL

        casiNormalizado=arrayImagen/arrayImagen.max()


        miniFoto=casiNormalizado.min()
        maxiFoto=casiNormalizado.max()

        for x in range(len(casiNormalizado)):
            for y in range(len(casiNormalizado[x])):
                if casiNormalizado[x][y] == miniFoto:
                    casiNormalizado[x][y] = miniMat
                elif casiNormalizado[x][y] == maxiFoto:
                    casiNormalizado[x][y] = maxiMat
                else: 
                    casiNormalizado[x][y] = ((casiNormalizado[x][y])*(maxiMat-miniMat)) + miniMat
            conValoresReales=casiNormalizado


        if normalizada==False :        
            return conValoresReales     

        else:
            #print(casiNormalizado)

            rango = ValorMaximoPosible - ValorMinimoPosible

            matrizNormalizadaEnAbsolutos = (conValoresReales-ValorMinimoPosible)/rango

            return matrizNormalizadaEnAbsolutos 
    except:
        print('matriz no ajustable')
        return -9999

'''
a partir de la capa de fuel de landfire detecatamos los bosques

si al recoger la matriz de 13km2 de tipos de fuel, se detecta que la mayoria de los datos corresponden a los valrores siguientes:

91 Urban 92 Snow/Ice 93 Agriculture 98 Water 99 Barren

se descatan los puntos.

PARA CONVERTIR LAS 13 CATEGORIAS DE FUEL A VALORES NOS BASAMOS EN EL PAPER Fire models and methods to map fuel types: The role of remote sensing

de este recogemos el fuel Loading (tonelada por hectarea) de 1h:

1=0.74 2=2 3=3.01 4=5.01 5=1 6=1.5 7=1.13 8=1.5 9=2.92 10=3.01 11=1.5 12=4.01 13=7.01

'''




#esta modificacion de la funcion isForest devuelve una matriz de 0 a 13 siendo 0 todos los datos vacios o no bosque
# si la mayoria de los datos son no bosque (agua, ciudad, etc) devuelve -9999
# si el punto central no es bosque tb devuelve -9999


def esBosque(matriz):
    ls=matriz.flatten()
    #Convertimos todos los datos en una lista de 0 a 13. los datos mayores de 13 tb se convierten en 0
    ls = [0 if x >13 else x for x in ls]     
    ls = [0.74 if x == 1 else x for x in ls]          
    #ls = [2 if x == 2 else x for x in ls] 
    ls = [3.1 if x == 3 else x for x in ls]
    
    ls = [5.01 if x == 4 else x for x in ls]          
    ls = [1 if x == 5 else x for x in ls] 
    ls = [1.5 if x == 6 else x for x in ls]
    
    ls = [1.13 if x == 7 else x for x in ls]          
    ls = [1.5 if x == 8 else x for x in ls] 
    ls = [2.92 if x == 9 else x for x in ls]
    
    ls = [3.01 if x == 10 else x for x in ls]          
    ls = [1.5 if x == 11 else x for x in ls] 
    ls = [4.01 if x == 12 else x for x in ls]
    
    ls = [7.01 if x == 13 else x for x in ls]          
    
    
    #si el punto central de la lista (de la matriz que es cuadrada) es 0 no es bosque y no nos sirve
    posicionCentral = np.floor(len(ls)/2)

    #recogemos la moda
    c=Counter(ls)
    modageneral=c.most_common(1)[0][0]    
    
    
    if(ls[int(posicionCentral)]==0):
        print("El valor central de la matriz no es un bosque")
        return -9999


    else:
        if(modageneral == 0):
            print("La moda no es un bosque")
            return -9999


        else:
            matrizDe0a13 = np.reshape(ls, (matriz.shape))

            return matrizDe0a13
        
        
        
        
# queremos recuperar una matriz de 12.5 de lado que dividiremos en 25 casillas de 500m cada una
# En caso de que mas de la mitad de los puntos alrededor o de que el punto central de la matriz no sean forest (segun la calsificacion de fuel) devuelve -9999

def coord2MatrixTOPO(longWGS,latWGS,boundary):
    km2=12.5
    minimosMaximos=[[-86, 4415], [0, 85], [-1, 359],[0,7.1]]
    
# YA NO LO NECESITO PQ YA HE CREADO UN LISTADO DE COORDENADAS RANDOM DENTRO DEL AREA DE INVESTIGACION
    if estaDentroTIF(longWGS,latWGS,boundary)==False:
        print('Fuera del marco de informacion!!!')
        return -8888   
    
    
    deESPG=4326
    aESPG=5070
      
    demTif='recortes/demTif.tif'
    sloTif='recortes/sloTif.tif'
    aspTif='recortes/aspTif.tif'
    
    #es de clasificiacion
    fueTif='recortes/fueTif.tif'
    
    coordenadaCentral=GeoPointsTranslator(longWGS,latWGS,deESPG,aESPG)
    coordenadaCentral[0],coordenadaCentral[1]

    #5070 esta en metros por lo que aqui podemos elegir los metros que queremos
    c=(km2*1000)/2
    #c=1500 #3km2
    
    #al crear la matriz final, en algunos casos se generaba una linea vacia en alguno de los lados
    c+=60 #anadimos dos pixels por lado que luego borraremos

    extremo00=coordenadaCentral[0]-c,coordenadaCentral[1]-c
    extremo01=coordenadaCentral[0]+c,coordenadaCentral[1]-c
    extremo10=coordenadaCentral[0]-c,coordenadaCentral[1]+c
    extremo11=coordenadaCentral[0]+c,coordenadaCentral[1]+c
    
    df = gpd.GeoDataFrame([['box', Point(extremo00)],
                        ['box', Point(extremo10)], 
                        ['box', Point(extremo11)], 
                        ['box', Point(extremo01)]],  
                     columns = ['shape_id', 'geometry'], 
                     geometry='geometry')
    df['geometry'] = df['geometry'].apply(lambda x: x.coords[0])
    df = df.groupby('shape_id')['geometry'].apply(lambda x: Polygon(x.tolist())).reset_index()

    # Declare the result as a new a GeoDataFrame
    poligonoDerecogida = gpd.GeoDataFrame(df, geometry = 'geometry')

    
    
    atributos=[demTif,sloTif,aspTif,fueTif] #,vegTif]
    trozos=[]
    
    
    
    for tifEntreComillas in atributos: 
        
        tiiif = rasterio.open(tifEntreComillas)
        
        poligonoDerecogida.crs=tiiif.crs
        poligonoDerecogida.to_file("poligonoDerecogida/poligonoDerecogida.shp")
        
    
    #para silenciar
    #poligonoDerecogida.plot()
    
        with fiona.open("poligonoDerecogida/poligonoDerecogida.shp", "r") as shapefile:
            shapes = [feature["geometry"] for feature in shapefile]
    
        try:

            with rasterio.open(tifEntreComillas) as src:
                out_image, out_transform = rasterio.mask.mask(src, shapes, crop=True)
                out_meta = src.meta

                out_meta.update({"driver": "GTiff",
                             "height": out_image.shape[1],
                             "width": out_image.shape[2],
                             "transform": out_transform})

            with rasterio.open("recorte.tif", "w", **out_meta) as dest:
                dest.write(out_image)

            tros= rasterio.open("recorte.tif")

        except:
            print('el recorte esta vacio')
            return -9999

    #para silenciar
        #plot.show(tros)

        a=tros.read()
        b=a[0]

        for x in range(len(b)):
            for n in range(len(b[x])):
                if b[x][n] == -9999:
                    b[x][n]=0
                    
                    
        #le restamos los 2 pixels por lado que le heemos anyadido anteriormente
        mat = b[2:(len(b)-2), 2:(len(b)-2)]
                    
        trozos.append(mat)
   
    #return trozos

#TODAS MENOS LA DE VEGETACION (QUE ES CATEGORICA)

    m25x25x4=[]
    
    #miramos la matriz de fuel(la ultima): si es bosque devuelve una matriz si no lo es devuelve -9999
    fuelA13=esBosque(trozos[len(trozos)-1])
    
    if isinstance(fuelA13,int):
        print("No es un bosque")
        return -9999

    
    #normalizamos las matrices menos la de fuel
    else:
        
        for x in range(len(trozos)-1):

            matF=prepararMatrix(trozos[x], minimosMaximos[x][0],minimosMaximos[x][1], numeroPixels=25, normalizada=True)

            m25x25x4.append(matF)
        
        #ahora normalizamos la matriz de fuel acotada por esBosque (aunque es categorica *13 podemos reecuperar los valores originales)
        matF=prepararMatrix(fuelA13,minimosMaximos[len(trozos)-1][0],minimosMaximos[len(trozos)-1][1])
        m25x25x4.append(matF)

                   
    return m25x25x4


#Para no perder INFORMACION, movemos las coordenadas un poco alrededor POR SI DAN SOBRE UNA RAYA DEL BOUNDARY
def moveAround(long,lat,boundary):
    noVa=True
    valor=0.001
    while noVa==True:
        lo,la=long-valor,lat+valor
        matrizADAN=coord2MatrixTOPO(lo,la,boundary)
        if matrizADAN == -9999:
            lo,la=long+valor,lat+valor
            matrizADAN=coord2MatrixTOPO(lo,la,boundary)
            if matrizADAN == -9999:
                
                valor=0.001
                lo,la=long-valor,lat-valor
                matrizADAN=coord2MatrixTOPO(lo,la,boundary)
                if matrizADAN == -9999:
                    
                    valor=0.001
                    lo,la=long+valor,lat-valor
                    matrizADAN=coord2MatrixTOPO(lo,la,boundary)
                    if matrizADAN == -9999:
                        print('no se puede')
                        return -9999
        noVa=False
    return (lo,la)   

#las matrices y el df ya han sido guardados


# 2.B GUARDAR FUNCIONES PARA TOPOGRAFIA
    
def guardarMatricesYdfTOPO(df,boundary,nombreCR_TOPOentreComillas):  #df=dfPuntosYosemite
    

    listaDeFallos=[]

    total=len(df)
    contador=0

    matrizTOPO=[]

    for punto in range(total):

        print(f'{contador} de {total}')
        start = time.time()

        if estaDentroTIF(df['long'][punto],df['lat'][punto],boundary)==False:
            listaDeFallos.append(indice)

            print('Punto fuera del marco de informacion')

        else:
            #coord2MatrixTOPO() missing 3 required positional arguments: 'km2', 'minimosMaximos', and 'boundary'
            matrizADAN=coord2MatrixTOPO(df['long'][punto],df['lat'][punto],boundary)


            if matrizADAN == -9999:
                # muevo el punto de ignicion 1km alrededor y lo vuelvo a pasar por la capturadora de matrices
                movido=moveAround(df['long'][punto],df['lat'][punto],boundary)

                if movido==-9999:
                    listaDeFallos.append(punto)

                else:
                    Long2,Lat2=movido
                    matrizADAN=coord2MatrixTOPO(Long2,Lat2,boundary)
                        #anyado la info con las nuevas coordenada al df
                    matrizTOPO.append(matrizADAN)                    

                        #guardo las nuevas coordenadas como punto de ignicion
                    df.at[punto,'long']=Long2
                    df.at[punto,'lat']=Lat2
                    df.at[punto,'datos']="Nuevas Coordenadas"

            else:
                #anyado la info con las nuevas coordenada al df
                matrizTOPO.append(matrizADAN)

                df.at[punto,'datos']="Con datos"

            end = time.time()
            print(end - start) 

        contador+=1


    direccion=('dfTERRENO/'+nombreCR_TOPOentreComillas+'.csv')
    df.to_csv(direccion)


    direccion=('matricesTerreno/'+nombreCR_TOPOentreComillas+'.pkl')
    with open(direccion, 'wb') as f:
        pickle.dump(matrizTOPO, f)

    end = time.time()
    print(end - start) 
    
    return (df,matrizTOPO)


 

# 3. RECOGEMOS LOS DATOS CLIMATOLOGICOS DEL DIA EN NC Y LOS PASAMOS A DF


In [4]:
#3. CREACION DE UNA MATRIZ DE 5 X 5 DE LOS PIXELS ORIGINALES DE WHEADER QUE SON DE CASI 3KM POR LADO (UNOS 15KM) 
#Y QUE POR LO TANTO RECOGEN MAS DE LOS 12.5 KM QUE NECESITAMOS
###_____________________________________
#la funcion creardatos podria incluir las esquinas de la fiuncion creacionPuntosHeatMap() que estan en 



# 3_RECOGEMOS LOS DATOS CLIMATOLOGICOS DEL DIA EN NC Y LOS PASAMOS A DF





def LatLon_TO_index(lat, lon):
    nrow=320
    ncol=256
    latmin=33.89
    latmax=42.45
    lonmin=-125.42
    lonmax=-116.59

    iiStep = (latmax - latmin) / nrow
    jjStep = (lonmax - lonmin) / ncol
    
    ii = (  latmax - lat  ) / iiStep  
    jj = (lon - lonmin) / jjStep  
    return (nrow-ii, jj)



def _____LatLon_To_index_BruteForce(path,lat,lon):
     with Dataset(path, "r") as ncin:
        nrow=320
        ncol=256
        XLAT = ncin.variables["XLAT"]
        XLON = ncin.variables["XLONG"]
        closest_ii=-1
        closest_jj=-1
        dis=999999
        for ii in range(nrow):
            for jj in range(ncol):
                _lat=XLAT[0,ii,jj]
                _lon=XLON[0,ii,jj]
                distance=(lat-_lat)**2+(lon-_lon)**2
                if distance<dis:
                    dis=distance
                    closest_ii=ii
                    closest_jj=jj
                    
        return (closest_ii,closest_jj)




def GetRaster(lat,lon,path,varname):
    
    if estaDentroNETCDF(lon,lat)==False:
        ras=np.zeros([5,5])
        return ras
    else:
    
        with Dataset(path, "r") as ncin:

            ii,jj=LatLon_TO_index(lat,lon)

            ras=np.zeros([5,5])

            myVar = ncin.variables[varname]

            for _i in range(5):
                for _j in range(5):

                    myii=ii-2+_i
                    myjj=jj-2+_j
                    f00=np.mean(myVar[:,myii , myjj])
                    f10=np.mean(myVar[:,myii +1, myjj])
                    f01=np.mean(myVar[:,myii , myjj +1])
                    f11=np.mean(myVar[:,myii+1 , myjj+1])
                    y=ii-int(ii)
                    x=jj-int(jj)

    #puesto que hay zonas en que los puntos de recogida estan a mas de 3 km y que estamos recogiendo el punto mas cercano a las coordinadas entradas, para evitar que se repitan valores intentamos interpolar los puntos para acercarnos mas a la situacion real entre puntos
    #bilinear interpolation

                    ras[_i][_j]=f00*(1-x)*(1-y)+f01*x*(1-y)+f10*(1-x)*y+f11*x*y

            return ras
                
                
#aa= GetRaster(35.0,-118,"nc/wrf_LT_d03_2010-11-13.nc","U10")   
#print(aa)




def cordAmatrizRapido(longx,latx,netcdfDELDIA):

    #EL ORDEN ORIGINAL ERA atributoS =['lfm',  'U10','V10', 'mean_wtd_moisture_1hr']
    #PERO AL MIRAR DATOS CONCRETOS PARECIA ESTAR CAMBIADO 
    #MANTENGO EL ORDEN PERO PODRIA HABER UN ERROR

    
    atributoS =['lfm',  'U10','V10', 'mean_wtd_moisture_1hr'] 

    matriz3D=[]
    for x in atributoS:
        
        m=GetRaster(latx,longx,netcdfDELDIA,x)   


        matriz3D.append(m)

    return matriz3D


#netcdfDELDIA="nc/wrf_LT_d03_2010-11-13.nc"
#m8S=cordAmatrizRapidoNUEVO(-121.523590,41.771904,netcdfDELDIA)
#m8S





# puesto que estamos con fuegos de california y sabemos que el nc solo corta al este y al sur nos aseguramos de que los fuegos mas alla no enttran.
# este limite se hace mas de 6km antes del borde del netcdf para que pueda recoger datos alrededor del punto requerido
def estaDentroNETCDF(long,lat): #=boundary):
    estaDentro=True
    if lat < 34 or long > -117:
        estaDentro=False
    return estaDentro





# 3,B CREAMOS UNA FUNCION QUE A PARTIR DE UNA MATRIZ DADA LA NORMALIZA 
#Y LA CONVIERTE EN UNA MATRIZ DE 27X27 
#DE LA QUE POSTERIORMENTE PODREMOS EXTRAER matrices 9 matrices de 25x25 PARA LA RED NEURONAL 


def prepararMatrix(CapaMatriz, ValorMinimoPosible=-999,ValorMaximoPosible=-999, numeroPixels=25, normalizada=True):

    
   
    #pasamos el array a 1 dimension para poder cambiar Todos los datos extremos por el valor maximo
    a1D = CapaMatriz.reshape((len(CapaMatriz)*len(CapaMatriz[0])),1)

    #creamos un contador de extremos (si hubiera muchos, posiblemente habria un problema con el supuesto valor maximo)
    contadorExtremos0 = 0
    if ValorMinimoPosible != -999:
        for valor in range(len(a1D)):
            if a1D[valor] < ValorMinimoPosible:
                a1D[valor] = ValorMinimoPosible

                contadorExtremos0 = contadorExtremos0+1
       
        #printLog(f"Se han encontrado {contadorExtremos0} elementos extremos que se han substituido por el valor minimo: {ValorMinimoPosible}")       
        if contadorExtremos0>2:
            printLog(printLog(f"Se han encontrado {contadorExtremos0} elementos extremos que se han substituido por el valor minimo: {ValorMinimoPosible}"))       

    else:
        #Si estos valores no estuvieran saldrá un aviso
        ValorMinimoPosible=0
        printLog("falta el valor minimo posible de este atributo")

 
    contadorExtremos = 0

    if ValorMaximoPosible != -999:
        for valor in range(len(a1D)):
            if a1D[valor] > ValorMaximoPosible:
                a1D[valor] = ValorMaximoPosible
                contadorExtremos = contadorExtremos+1

        #printLog(f"Se han encontrado {contadorExtremos} elementos extremos que se han substituido por el valor maximo: {ValorMaximoPosible}")       
        if contadorExtremos0>2:
            printLog(printLog(f"Se han encontrado {contadorExtremos0} elementos extremos que se han substituido por el valor minimo: {ValorMinimoPosible}"))       
                  
    else:
        #Si estos valores no estuvieran saldrá un aviso
        ValorMaximoPosible=50
        printLog("falta el valor maximo posible de este atributo")
        
        

    try:

        #devolvemos el array a la matriz original SIN LOS VALORES EXTREMOS
        XArray = a1D.reshape(len(CapaMatriz),len(CapaMatriz[0]))
    #printLog(f"Sin extremos:\n{XArray}")

        #guardamos los max y minimos de la matriz original
        miniMat=XArray.min()
        maxiMat=XArray.max()
    #printLog(miniMat)

        XArrayA0 = (XArray-XArray.min()) #esto mueve el rango de 0 a max
        arrayNorm0_1 = XArrayA0/XArrayA0.max() #esto lo normaliza
    #printLog(f"Normalizada:{arrayNorm0_1}") #Esto es con lo que alimentaremos la imagen para la creacion o fusion de N pixels


        #convertimos el array en una imagen con valor min = 0 azul y max = 255 amarillo
        img = Image.fromarray((arrayNorm0_1 * 255).astype(np.uint8))
    #plt.matshow(img)
        #convertimos la imagen en matriz
        img2 = img.resize((numeroPixels, numeroPixels), Image.BICUBIC) #ANTIALIAS) #BILINEAR) NEAREST

        arrayImagen = np.array(img2, copy=True)

        #printLog(f"Nuevo Tamanyo:\n{arrayImagen}")

        # CONVERSION DE LA IMAGEN EN COLOR MODIFICADA O NO, A UNA MATRIZ EN BASE A LOS MAXIMOS Y MINIMOS DE LA MATRIZ ORIGINAL

        casiNormalizado=arrayImagen/arrayImagen.max()


        miniFoto=casiNormalizado.min()
        maxiFoto=casiNormalizado.max()

        for x in range(len(casiNormalizado)):
            for y in range(len(casiNormalizado[x])):
                if casiNormalizado[x][y] == miniFoto:
                    casiNormalizado[x][y] = miniMat
                elif casiNormalizado[x][y] == maxiFoto:
                    casiNormalizado[x][y] = maxiMat
                else: 
                    casiNormalizado[x][y] = ((casiNormalizado[x][y])*(maxiMat-miniMat)) + miniMat
            conValoresReales=casiNormalizado


        if normalizada==False :        
            return conValoresReales     

        else:
            #printLog(casiNormalizado)

            rango = ValorMaximoPosible - ValorMinimoPosible

            matrizNormalizadaEnAbsolutos = (conValoresReales-ValorMinimoPosible)/rango

            return matrizNormalizadaEnAbsolutos 
    except:
        printLog('matriz no ajustable')
        return -9999

    
    

    
    
# 5. FUNCION DE RECOGIDE DATOS 

def ncCoord2cnnMatrix3DDD(long, lat,netcdfDELDIA): #puedo quitar el geodrataframe?
    
    if estaDentroNETCDF(long, lat)==False:
        return -9999
    
    matrizLFM_25=cordAmatrizRapido(long,lat,netcdfDELDIA) #puedo quitar el geodrataframe?
    if matrizLFM_25 == -9999:
        return -9999

    

    #### ES NECESARIO ESTABLECER LOS MINIMOS Y MAXIMOS:
    v_LFM=[0,300]
    v_U10=[-20,+20]
    v_V10=[-20,+20]    
    v_MO1=[0,1]


    atributoS =[v_LFM, v_U10, v_V10, v_MO1]  
    

    #ESTA MATRIZ REPRESENTA 15KM a 3KM POR PIXEL (25pixels),  PERO NOSOTROS SOLO QUEREMOS 12.5KM
    # asi que dividimos cada pixel en 6 partes:  25*12=300  pixels de 250m 
    # si recortamos 5 pixels por lado

    m25x25x4=[]
    for atr in range(4):
        
        m150=prepararMatrix(matrizLFM_25[atr],atributoS[atr][0],atributoS[atr][1],150)


    #Ahora cada pixel representa 100m, cotamos 8 y 7 pixels por lado para reducir 1.5km que nos sobran
        X1 = m150[8:153, 8:153]
    #plt.matshow(X1)
    #plt.colorbar()

    #agrupamos los valores para devolver una matiz de 25 x 25 pixels que representan 500m de lado, cada pixel
    #Ahora el maximos siempre es 1 i el minimo 0 pq ya esta normalizada!!
        m25F=prepararMatrix(X1,0,1,25)
        m25x25x4.append(m25F)
    #plt.matshow(m25F)
    #plt.colorbar()
    return m25x25x4



# 6. A PARTIR DEL DF CON TODOS LOS FUEGOS CON DATOS SE PREPARA EL DF PARA LOS DATOS FINALES X ANYOS
#ESTAS SON LAS COORDENADAS DEFINITIVAS CON INFORMACION TOPOGRAFICA (ya tienen maties organizadas x anyos en este orden)


def prepararNuevoDF():
    direccion=('dfTERRENO/yosemite.csv')
    dfFuegosTopo = pd.read_csv(direccion, index_col=0)

    dfFuegosTopo["indice"]=range(len(dfFuegosTopo))
    dfFuegosTopo["meteo"]='Sin Datos'

    return dfFuegosTopo



#AQUI EMPIEZA LA FUNCION DE CREACION DE MATRICES DE DATOS METEOROLOGICOS para YOSEMITE:
#(es una modificacion de la funcion de entrada: matizMeteoXanyo(dfDelAnyo,anyo, boundary)

# en este caso la fecha entra por el df generado a partir de netcdf = datospoli




def matizMeteoYOSEMITE(dfYOSEMITE,netcdfDELDIA):

    
 
    #matrizMeteoFuegoAnyo=[]
    matrizMeteoYOSEMITE=[]
    
    #NO HACE FALTA 
    #matrizMeteoNO_FuegoAnyo=[]   NO HACE FALTA 
    #abrimos la lista de puntos random sin fuego posibles del anyo a tratar
    #direccion=('dfRandomNOfuegoConDatos/dfFinalNOfuego'+str(anyo)+'.csv')
    #dfNOFuegoAnual = pd.read_csv(direccion, index_col=0)
    
    #for posicion in range(len(dfDelAnyo)):   
    #RECORREMOS TODAS LOS PUNTOS DE LOS QUE TENEMOS DATOS TOPOGRAFICOS
    for posicion in range(len(dfYOSEMITE)):     
        start = time.time()
        # SE REPITE LA FECHA Y HAY DATOS
        #TODOS SON LA MISMA FECHA POR LO QUE SOLO RECOGEMOS LA POSICION
        long=float(dfYOSEMITE['long'][posicion])
        lat=float(dfYOSEMITE['lat'][posicion])
        print(long,lat)

        
        
        #CONVERTIMOS EL NCDF EN UN DF
        #datospoli=meteoAmatriz(datosEntrecomillas=ncdf)
    #aqui recogemos la matriz para esta posicion    
    
        
        matrizMeteoFuegodia=ncCoord2cnnMatrix3DDD(long,lat, netcdfDELDIA)
        if matrizMeteoFuegodia==-9999:
            print("no tiene datos meteorologicos")

    #SI EL FUEGO NO TIENE DATOS SE ACABA AQUÍ y PASA AL SIGUIENTE FUEGO 

        else:
            #imprimimos el primer numero central de la primera matriz para ver si funciona (que no se repita el mismo)
            print(matrizMeteoFuegodia[0][0][14])
            #guardamos la matriz con las matrices del anyo
            matrizMeteoYOSEMITE.append(matrizMeteoFuegodia)

            #anotamos que tiene matriz en el df
            dfYOSEMITE.at[posicion,'meteo']="Con datos"
        end = time.time()
        print(end - start) 
               
    direccion=('dfTERRENO/yosemiteCompleto.csv')
    dfYOSEMITE.to_csv(direccion)

    
    direccion=('matricesTerreno/matricesYOSEMeteo.pkl')
    with open(direccion, 'wb') as f:
        pickle.dump(matrizMeteoYOSEMITE, f)

    return (dfYOSEMITE,matrizMeteoYOSEMITE)
    
    
        
def printLog(a):
    print(a)
    f.write(f'{a} \n')




  

# 4. COMBINAR MATRICES Y PREPARAR PARA CNN!

In [5]:

def matrizFINAL25x25x8(dfYOSEMITE_TOTAL,topo,meteo):

    YOSEMITE25x25x8=[]
    dfYOSEMITE_TOTAL['MATRIZ_FINAL']="CON DATOS"

    contadorDeMATRICES=0
    for x in range(len(dfYOSEMITE_TOTAL)):
        # seleccionamos las posiciones de dfmatricesTopo_Meteo2019 que tienen datos

        if (dfYOSEMITE_TOTAL['datos'][x]!='Sin datos') and (dfYOSEMITE_TOTAL['meteo'][x] == 'Con datos'):


            YOSEMITE25x25x8.append(topo[contadorDeMATRICES]+meteo[contadorDeMATRICES])
            contadorDeMATRICES+=1
            #print(f'LA MATRIZ {contadorDeMATRICES}Se ha guardado la posicion {x} del dfYOSEMITE_TOTAL')
        
        else:
            print(f'Faltan datos en la posicion {x}')
            
            dfYOSEMITE_TOTAL.at[x,'MATRIZ_FINAL']= "SIN DATOS"
    
    direccion=('matricesTerreno/matricesYOSEx8.pkl')
    
    with open(direccion, 'wb') as f:
        pickle.dump(YOSEMITE25x25x8, f)
        
    direccion=('dfTERRENO/yosemitePROYECCION.csv')
    dfYOSEMITE_TOTAL.to_csv(direccion)
    

    
    return YOSEMITE25x25x8,dfYOSEMITE_TOTAL



def resultadoYproyeccion(YOSEMITE25x25x8,dfYOSEMITE_TOTAL):
    #print(dfYOSEMITE_TOTAL)
    x_base = np.array(YOSEMITE25x25x8)
    
    print(x_base.shape)
    
    nas=0
    for lista in range(len(x_base)):
        for matriz in range(8):
            where_are_NaNs = np.isnan(x_base[lista][matriz])
            x_base[lista][matriz][where_are_NaNs] = 0
            nas+=1

    print(f'Se han eliminado {nas} NANs')
    
    
    
        #reordenamos los datos para que sean (400, 25, 25, 8)
    
    print(x_base.shape)
    
    x_base=x_base.transpose (0,2,3,1)


    #cargamos el modelo ya entrenado
    reconstructed_model = keras.models.load_model('modelos/my_h5_modelMEJOR_PLUS_shuffled94.h5')


    
    # hacemos una prediccion y ordenamos los resultados
    pred = reconstructed_model.predict(x_base) 

    #CREAMOS LISTA CON LOS DATOS QUE TENEMOS TENIENDO EN CUENTA QUE PUEDE HABRER CASILLAS VACIAS.
    #print(pred)
    probabilidadIgnicion=[]
    for x in range(len(pred)):
        probabilidadIgnicion.append(pred[x][0])
    
    #print(probabilidadIgnicion)
    npred=0
    dfYOSEMITE_TOTAL['prediccion']=0.0
    for x in range(len(dfYOSEMITE_TOTAL)):

        if dfYOSEMITE_TOTAL['MATRIZ_FINAL'][x]=="CON DATOS":
            #print(npred,probabilidadIgnicion[npred])
            
            
            dfYOSEMITE_TOTAL.at[x,'prediccion']= probabilidadIgnicion[npred]
            npred+=1
    #print(dfYOSEMITE_TOTAL)
    
    #yosemite

    direccion=('dfTERRENO/yosemiteConPREDICCION.csv')
    dfYOSEMITE_TOTAL.to_csv(direccion)
    
    return dfYOSEMITE_TOTAL
    


# 5. la funcion final!

In [6]:
  
    
# la funcion final!

def lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2014-07-22' ,tamanyoLadoMapaMetros=30000,PrecisionX10KmDeLado= 60):
    #maximo 2 puntos por quilometro: ej 10000-20 
    
    start = time.time()
        
    netcdfDELDIA="nc/wrf_LT_d03_"+fecha+".nc"

   

    dfPuntosYosemite, esquinasTif = creacionPuntosHeatMap(long=x,lat=y,tamanyoLadoMapaMetros=tamanyoLadoMapaMetros,precisionX10KmDeLado=PrecisionX10KmDeLado)

    #esta funcion crea los tifs que necesitamos para recorrer el terreno deseado todos los resultados de topografia en 
    #PERO PARA QUE FUNCIONA NECESITA LOS TIFS DE TODA CALIFORNIA QUE SON MUY PESADOS
    #EN ESTE CASO YA SE HAN RECORTADO LOS TIFS PARA EL ANALISIS DE 40KM DE LADO DE YOSEMITE,
    #LOS TIFS REPRESENTAN 40KM DE LADO + 7KM POR LADO DE BUFFER PARA LA CNN = 54KM DE LADO

    #se han considerado los valores estandart de climatologia (para cualquier punto) 
    #humedad en naturalez viva : v_LFM=[0,300]
    #dirección del viento : v_U10=[-20,+20]
    #velocidad del viento : v_V10=[-20,+20]    
    #humedad en naturalez muerta : v_MO1=[0,1]
    
    #como la informacion topografica no cambia, primero se comprueba si ya se han calculado (y se han guardado)estas entradas anteriormente 
    #si se ya esta guardada no hace faltar recalcularla, basta con calcular la metereologia que si que cambia.
    #NO SE GUARDA LA FECHA SOLO LA POSCION, EL TEMANYO Y EL NUMERO DE PIXELS
    nombreCR_TOPOentreComillas="EN"+str(x) + "_" + str(y) + "A" + str(tamanyoLadoMapaMetros/1000) + "kmXlado"+ str(PrecisionX10KmDeLado)+"puntosXkm_TOPOGRAFIA"  
###
    try:
        direccion=("matricesTerreno/"+nombreCR_TOPOentreComillas+".pkl")  
        with open(direccion, 'rb') as f:
            matrizTopo=pickle.load(f)
            print("matrices de datos topograficos YA CREADOS ANTERIORMENTE")
            
            
            direccion=('dfTERRENO/'+nombreCR_TOPOentreComillas+'.csv')
            df = pd.read_csv(direccion, index_col=0)
            print("df de datos topograficos tb Cargados")           
            
        
    except IOError:
        print("HAY QUE CREAR LOS DATOS TOPOGRAFICOS")
        #si no las hemos calculado antes las calculamos ahora
        
        #boundary has es una red creada especilamente para este programa, que cubre los puntos que incluyen los ncdf con los que contamos 
        boundary=gpd.read_file("poligonoMeteo/nc_shrinkboundary.shp")
        #se crean los shapefiles para la captura
        tifAnalisis(x, y, esquinasTif, boundary)


        #esta funcion lanza todo el proceso de recogida de datos TOPOGRAFICOS
        df,matrizTopo=guardarMatricesYdfTOPO(dfPuntosYosemite,boundary,nombreCR_TOPOentreComillas)
        #df,matrizTopo=guardarMatricesYdfTOPO(dfPuntosYosemite, boundary)

    
    
    #esta funcion lanza todo el proceso de recogida de datos METEOROLOGICOS
    dfYOSEMITE_TOTAL,matrizMeteo=matizMeteoYOSEMITE(df, netcdfDELDIA)

    #esta funcion junta las dos matrices
    YOSEMITE25x25x8,dfYOSEMITE_TOTAL2=matrizFINAL25x25x8(dfYOSEMITE_TOTAL,matrizTopo,matrizMeteo)
    len(YOSEMITE25x25x8),len(YOSEMITE25x25x8[0])

    #4. PASAMOS EL RESULTADO POR LA RED NEURONAL

    dfYOSEMITE_TOTAL_F=resultadoYproyeccion(YOSEMITE25x25x8,dfYOSEMITE_TOTAL2)
    
    
    print(dfYOSEMITE_TOTAL_F)
    
    titulo=netcdfDELDIA[14:-3] + "EN"+str(x) + "_" + str(y) + "A" + str(tamanyoLadoMapaMetros/1000) + "kmXlado"+ str(PrecisionX10KmDeLado)+"puntosXkmET"
    direccion=('DFlistoParaHeatMap/'+titulo+'.csv')
    dfYOSEMITE_TOTAL.to_csv(direccion)

    end = time.time()
    print(f'\nPara calcular {PrecisionX10KmDeLado*PrecisionX10KmDeLado} puntos ha tardado {end - start}') 
    #dataframeDeResultados

    print(f'\nThe chances of fire in all the area is {dfYOSEMITE_TOTAL_F.prediccion.mean()}')

    yosemite=[]
    for x in range(len(dfYOSEMITE_TOTAL_F)):
        yosemite.append(dfYOSEMITE_TOTAL_F['prediccion'][x])

    n=len(yosemite)
    ns = np.ceil(np.sqrt(n)).astype(int)
    whiteWolf = np.reshape(yosemite,(ns,ns))


    #guardamos
    direccion=('matricesTerreno/heatmapWhitWolf.pkl')  
    with open(direccion, 'wb') as f:
        pickle.dump(whiteWolf, f)

# 6. INTRODUCIR DATOS

In [7]:
# LA PRIMERA VEZ Q SE INTRODUCE UN AREA CONCRETA SE CALCULAN LOS DATOS TOPOGRAFICOS 

In [16]:
def main():       
    lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2019-02-22' ,tamanyoLadoMapaMetros=50000,PrecisionX10KmDeLado=10)

if __name__ == "__main__":
    main()

Se recoge un punto cada 5000.0 metros
EL MAPA SE BASARA EN 121 PUNTOS DE INFORMACION

Las esquinas del mapa son:
((-119.97615349567953, 37.5784913526509), (-119.97615349567953, 38.12114390070092), (-119.51596984159855, 37.63885824224389), (-119.51596984159855, 38.18134878833835))
matrices de datos topograficos YA CREADOS ANTERIORMENTE
df de datos topograficos tb Cargados
-119.97615349567951 37.5784913526509
0.2762327019250449
0.5419468879699707
-119.97615349567951 37.63885824224389
0.2788491875918688
0.4584038257598877
-119.97615349567951 37.69920703456011
0.2719593692932158
0.444979190826416
-119.97615349567951 37.759537754045475
0.27372483850045676
0.5053970813751221
-119.97615349567951 37.81985042506828
0.27431433362923807
0.45775318145751953
-119.97615349567951 37.88014507191898
0.2702327842038157
0.46624279022216797
-119.97615349567951 37.940421718810725


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:85: UserWarning: Warning: converting a masked element to nan.
/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:214: RuntimeWarning: invalid value encountered in true_divide


nan
0.5415701866149902
-119.97615349567951 38.00068038987917
nan
0.4829237461090088
-119.97615349567951 38.060921109182296
nan
0.4546370506286621
-119.97615349567951 38.12114390070092
nan
0.45112180709838867
-119.97615349567951 38.181348788338354
nan
0.5218508243560791
-119.93047215268996 37.5784913526509
0.2768753792866056
0.45268797874450684
-119.93047215268996 37.63885824224389
0.2762102106834598
0.4567592144012451
-119.93047215268996 37.69920703456011
0.27329448199546447
0.46121716499328613
-119.93047215268996 37.759537754045475
0.26958309924372637
0.4656848907470703
-119.93047215268996 37.81985042506828
0.27000852330852676
0.46260905265808105
-119.93047215268996 37.88014507191898
0.27076999154880277
0.4839160442352295
-119.93047215268996 37.940421718810725
nan
0.48389101028442383
-119.93047215268996 38.00068038987917
nan
0.4842801094055176
-119.93047215268996 38.060921109182296
nan
0.4799997806549072
-119.93047215268996 38.12114390070092
nan
0.48015832901000977
-119.93047215268996

# PERO AL CAMBIAR DE FECHA NO LOS NECESITA VOLVER A CALCULAR, AHORA SOLO BUSCA LOS METEREOLOGOGICOS

In [20]:
def main():       
    lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2019-02-22' ,tamanyoLadoMapaMetros=30000,PrecisionX10KmDeLado=60)

if __name__ == "__main__":
    main()

Se recoge un punto cada 500.0 metros
EL MAPA SE BASARA EN 3721 PUNTOS DE INFORMACION

Las esquinas del mapa son:
((-119.89387347275752, 37.6871387227045), (-119.89387347275752, 38.01272996911252), (-119.64135230825693, 37.69266159921349), (-119.64135230825693, 38.01824394389611))
HAY QUE CREAR LOS DATOS TOPOGRAFICOS


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/pandas/core/groupby/ops.py:958: FutureWarning:     You are passing non-geometry data to the GeoSeries constructor. Currently,
    it falls back to returning a pandas Series. But in the future, we will start
    to raise a TypeError instead.
  return type(sdata)(mgr, name=sdata.name, fastpath=True)


0 de 3721


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/pandas/core/groupby/ops.py:958: FutureWarning:     You are passing non-geometry data to the GeoSeries constructor. Currently,
    it falls back to returning a pandas Series. But in the future, we will start
    to raise a TypeError instead.
  return type(sdata)(mgr, name=sdata.name, fastpath=True)


5.21125602722168
1 de 3721


...

nan
0.4414851665496826
-119.68359651771289 37.89138445522785
nan
0.43567419052124023
-119.68359651771289 37.896901741749915
nan
0.4320189952850342
-119.68359651771289 37.90241887754443
nan
0.44350171089172363
-119.68359651771289 37.90793586262977
nan
0.4354832172393799
-119.68359651771289 37.913452697024624
nan
0.4385080337524414
-119.68359651771289 37.918969380747406
nan
0.43805480003356934
-119.68359651771289 37.92448591381657
nan
0.4434828758239746
-119.68359651771289 37.930002296250684
nan
0.4361140727996826
-119.68359651771289 37.9355185280682
nan
0.43361401557922363
-119.68359651771289 37.94103460928765
nan
0.4338831901550293
-119.68359651771289 37.94655053992747
nan
0.43186306953430176
-119.68359651771289 37.95206632000607
nan
0.43387770652770996
-119.68359651771289 37.95758194954203
nan
0.43499112129211426
-119.68359651771289 37.963097428553745
nan
0.43706607818603516
-119.68359651771289 37.96861275705972
nan
0.43528318405151367
-119.68359651771289 37.97412793507838
nan
0.44531

nan
0.4787719249725342
-119.675152728257 37.963097428553745
nan
0.4712831974029541
-119.675152728257 37.96861275705972
nan
0.48518967628479004
-119.675152728257 37.97412793507838
nan
0.46897029876708984
-119.675152728257 37.97964296262812
nan
0.47219085693359375
-119.675152728257 37.985157839727485
nan
0.4673919677734375
-119.675152728257 37.99067256639475
nan
0.4753410816192627
-119.675152728257 37.9961871426485
nan
0.47295475006103516
-119.675152728257 38.00170156850711
nan
0.4683041572570801
-119.675152728257 38.00721584398897
nan
0.4696931838989258
-119.675152728257 38.01272996911252
nan
0.4641268253326416
-119.675152728257 38.01824394389611
nan
0.4649200439453125
-119.67092988663478 37.6871387227045
nan
0.48322510719299316
-119.67092988663478 37.69266159921349
nan
0.47691988945007324
-119.67092988663478 37.69818432430598
nan
0.47417306900024414
-119.67092988663478 37.70370689800077
nan
0.46399593353271484
-119.67092988663478 37.70922932031643
nan
0.4689650535583496
-119.6709298866

nan
0.4385080337524414
-119.66248230897718 37.69266159921349
nan
0.4364039897918701
-119.66248230897718 37.69818432430598
nan
0.4380159378051758
-119.66248230897718 37.70370689800077
nan
0.4360520839691162
-119.66248230897718 37.70922932031643
nan
0.4366612434387207
-119.66248230897718 37.71475159127172
nan
0.446674108505249
-119.66248230897718 37.72027371088543
nan
0.4387240409851074
-119.66248230897718 37.72579567917622
nan
0.43422508239746094
-119.66248230897718 37.73131749616262
nan
0.4461028575897217
-119.66248230897718 37.73683916186356
nan
0.4337599277496338
-119.66248230897718 37.74236067629751
nan
0.43726301193237305
-119.66248230897718 37.74788203948328
nan
0.4394080638885498
-119.66248230897718 37.75340325143948
nan
0.43286609649658203
-119.66248230897718 37.758924312184746
nan
0.4359121322631836
-119.66248230897718 37.764445221737844
nan
0.4512951374053955
-119.66248230897718 37.76996598011727
nan
0.4373490810394287
-119.66248230897718 37.77548658734181
nan
0.43577122688293

nan
0.43665099143981934
-119.65403220460223 37.758924312184746
nan
0.4391591548919678
-119.65403220460223 37.764445221737844
nan
0.43665361404418945
-119.65403220460223 37.76996598011727
nan
0.4389071464538574
-119.65503220460224 37.77648658734181
nan
0.43355274200439453
-119.65403220460223 37.781007043430016
nan
0.4389770030975342
-119.65403220460223 37.786527348400526
nan
0.43363308906555176
-119.65403220460223 37.792047502272055
nan
0.4390890598297119
-119.65403220460223 37.79756750506312
nan
0.434467077255249
-119.65403220460223 37.80308735679241
nan
0.43039798736572266
-119.65403220460223 37.808607057478454
nan
0.43827271461486816
-119.65403220460223 37.81412660714
nan
0.42893004417419434
-119.65403220460223 37.81964600579557
nan
0.46178579330444336
-119.65403220460223 37.82516525346369
nan
0.4692821502685547
-119.65403220460223 37.83068435016305
nan
0.4678020477294922
-119.65403220460223 37.836203295912206
nan
0.4827721118927002
-119.65503220460224 37.842722090729765
nan
0.470983

nan
0.44560718536376953
-119.64557957250983 37.82516525346369
nan
0.43517208099365234
-119.64557957250983 37.83068435016305
nan
0.4361569881439209
-119.64557957250983 37.836203295912206
nan
0.4327700138092041
-119.64657957250984 37.84072209072977
nan
0.43798398971557617
-119.64557957250983 37.84724073463428
nan
0.43757081031799316
-119.64557957250983 37.85275922764433
nan
0.4368870258331299
-119.64557957250983 37.85827756977845
nan
0.43734097480773926
-119.64557957250983 37.86379576105518
nan
0.4428219795227051
-119.64557957250983 37.869313801493135
nan
0.43338489532470703
-119.64557957250983 37.87483169111085
nan
0.4548470973968506
-119.64557957250983 37.88034942992687
nan
0.4374678134918213
-119.64557957250983 37.88586701795969
nan
0.44472503662109375
-119.64557957250983 37.89138445522785
nan
0.46230602264404297
-119.64557957250983 37.896901741749915
nan
0.4420607089996338
-119.64557957250983 37.90241887754443
nan
0.4530496597290039
-119.64557957250983 37.90793586262977
nan
0.4515838

In [21]:
def main():       
    lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2014-07-22' ,tamanyoLadoMapaMetros=30000,PrecisionX10KmDeLado=60)

if __name__ == "__main__":
    main()

Se recoge un punto cada 500.0 metros
EL MAPA SE BASARA EN 3721 PUNTOS DE INFORMACION

Las esquinas del mapa son:
((-119.89387347275752, 37.6871387227045), (-119.89387347275752, 38.01272996911252), (-119.64135230825693, 37.69266159921349), (-119.64135230825693, 38.01824394389611))
matrices de datos topograficos YA CREADOS ANTERIORMENTE
df de datos topograficos tb Cargados
-119.8938734727575 37.6871387227045


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:85: UserWarning: Warning: converting a masked element to nan.
/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:214: RuntimeWarning: invalid value encountered in true_divide


nan
0.49329400062561035
-119.8938734727575 37.69266159921349
nan
0.4443182945251465
-119.8938734727575 37.69818432430598
nan
0.44168686866760254
-119.8938734727575 37.703706898000775
nan
0.43285083770751953
-119.89487347275751 37.71022932031643
nan
0.4333209991455078
-119.8938734727575 37.71475159127172
nan
0.4306681156158447
-119.8938734727575 37.72027371088543
nan
0.5018179416656494
-119.8938734727575 37.72579567917622
nan
0.43166184425354004
-119.8938734727575 37.73131749616262
nan
0.4338529109954834
-119.8938734727575 37.736839161863564
nan
0.4354569911956787
-119.8938734727575 37.74236067629751
nan
0.44414806365966797
-119.8938734727575 37.74788203948328
nan
0.4363527297973633
-119.8938734727575 37.75340325143948
nan
0.4350268840789795
-119.8938734727575 37.758924312184746
nan
0.4335670471191406
-119.8938734727575 37.764445221737844
nan
0.4385221004486084
-119.8938734727575 37.76996598011727
nan
0.4367790222167969
-119.8938734727575 37.77548658734182
nan
0.43511509895324707
-119.8

nan
0.4581592082977295
-119.8854924902026 37.764445221737844
nan
0.45646119117736816
-119.8854924902026 37.76996598011727
nan
0.45982813835144043
-119.8854924902026 37.77548658734182
nan
0.4496169090270996
-119.8854924902026 37.781007043430016
nan
0.4539799690246582
-119.8854924902026 37.78652734840053
nan
0.45901012420654297
-119.8854924902026 37.792047502272055
nan
0.4449801445007324
-119.8854924902026 37.79756750506312
nan
0.44217610359191895
-119.8854924902026 37.80308735679241
nan
0.4685180187225342
-119.8854924902026 37.808607057478454
nan
0.44504404067993164
-119.8854924902026 37.814126607140004
nan
0.4455287456512451
-119.8854924902026 37.81964600579557
nan
0.4537029266357422
-119.8854924902026 37.82516525346369
nan
0.44556403160095215
-119.8854924902026 37.83068435016305
nan
0.4460930824279785
-119.8854924902026 37.836203295912206
nan
0.44542503356933594
-119.8854924902026 37.841722090729775
nan
0.4407198429107666
-119.8854924902026 37.84724073463428
nan
0.4646151065826416
-11

nan
0.4408378601074219
-119.87710900727444 37.83068435016305
nan
0.4378209114074707
-119.87710900727444 37.836203295912206
nan
0.43393588066101074
-119.87710900727444 37.841722090729775
nan
0.4354548454284668
-119.87710900727444 37.84724073463428
nan
0.43337440490722656
-119.87710900727444 37.85275922764433
nan
0.4381260871887207
-119.87710900727444 37.85827756977845
nan
0.43572402000427246
-119.87710900727444 37.86379576105518
nan
0.43390798568725586
-119.87710900727444 37.869313801493135
nan
0.4335017204284668
-119.87710900727444 37.87483169111085
nan
0.433182954788208
-119.87710900727444 37.880349429926866
nan
0.4383389949798584
-119.87710900727444 37.88586701795968
nan
0.44620203971862793
-119.87710900727444 37.89138445522785
nan
0.43398404121398926
-119.87710900727444 37.89690174174992
nan
0.4339940547943115
-119.87710900727444 37.902418877544434
nan
0.435396671295166
-119.87710900727444 37.90793586262977
nan
0.4395880699157715
-119.87710900727444 37.913452697024624
nan
0.44065785

...

nan
0.4349181652069092
-119.68359651771289 37.83068435016305
nan
0.4362461566925049
-119.68359651771289 37.836203295912206
nan
0.43584775924682617
-119.68359651771289 37.841722090729775
nan
0.44428014755249023
-119.68359651771289 37.84724073463428
nan
0.43596887588500977
-119.68359651771289 37.85275922764433
nan
0.4456050395965576
-119.68359651771289 37.85827756977845
nan
0.4360158443450928
-119.68359651771289 37.86379576105518
nan
0.4352598190307617
-119.68359651771289 37.869313801493135
nan
0.44018125534057617
-119.68359651771289 37.87483169111085
nan
0.4358668327331543
-119.68359651771289 37.880349429926866
nan
0.44253087043762207
-119.68359651771289 37.88586701795968
nan
0.45627593994140625
-119.68359651771289 37.89138445522785
nan
0.43424367904663086
-119.68359651771289 37.89690174174992
nan
0.43537282943725586
-119.68359651771289 37.902418877544434
nan
0.4400367736816406
-119.68359651771289 37.90793586262977
nan
0.43091297149658203
-119.68359651771289 37.913452697024624
nan
0.447

nan
0.4401981830596924
-119.675152728257 37.89690174174992
nan
0.4373490810394287
-119.675152728257 37.902418877544434
nan
0.43615078926086426
-119.675152728257 37.90793586262977
nan
0.44503307342529297
-119.675152728257 37.913452697024624
nan
0.43644189834594727
-119.675152728257 37.918969380747406
nan
0.4328489303588867
-119.675152728257 37.92448591381657
nan
0.4355430603027344
-119.675152728257 37.930002296250684
nan
0.4439888000488281
-119.675152728257 37.9355185280682
nan
0.44045591354370117
-119.675152728257 37.94103460928765
nan
0.441148042678833
-119.675152728257 37.94655053992747
nan
0.43487000465393066
-119.675152728257 37.95206632000607
nan
0.43020081520080566
-119.675152728257 37.95758194954203
nan
0.4340248107910156
-119.675152728257 37.963097428553745
nan
0.43747401237487793
-119.675152728257 37.96861275705972
nan
0.43762874603271484
-119.675152728257 37.974127935078386
nan
0.4351806640625
-119.675152728257 37.97964296262812
nan
0.43571996688842773
-119.675152728257 37.98

nan
0.43376898765563965
-119.66670641358317 37.96861275705972
nan
0.43432021141052246
-119.66670641358317 37.974127935078386
nan
0.4443089962005615
-119.66770641358316 37.98064296262812
nan
0.44413280487060547
-119.66670641358317 37.98515783972749
nan
0.4477269649505615
-119.66670641358317 37.99067256639475
nan
0.4337599277496338
-119.66670641358317 37.9961871426485
nan
0.43664097785949707
-119.66670641358317 38.00170156850711
nan
0.43163514137268066
-119.66670641358317 38.007215843988966
nan
0.44333481788635254
-119.66670641358317 38.01272996911253
nan
0.43936800956726074
-119.66770641358316 38.01924394389611
nan
0.43505120277404785
-119.66248230897719 37.6871387227045
nan
0.43761777877807617
-119.66248230897719 37.69266159921349
nan
0.43605470657348633
-119.66248230897719 37.69818432430598
nan
0.4346151351928711
-119.66248230897719 37.703706898000775
nan
0.43250608444213867
-119.66248230897719 37.70922932031643
nan
0.434157133102417
-119.66248230897719 37.71475159127172
nan
0.4369449

nan
0.43585896492004395
-119.65403220460225 37.69266159921349
nan
0.43940305709838867
-119.65403220460225 37.69818432430598
nan
0.4387631416320801
-119.65403220460225 37.703706898000775
nan
0.4367649555206299
-119.65403220460225 37.70922932031643
nan
0.4367861747741699
-119.65403220460225 37.71475159127172
nan
0.44011688232421875
-119.65403220460225 37.72027371088543
nan
0.43729496002197266
-119.65403220460225 37.72579567917622
nan
0.437654972076416
-119.65503220460224 37.732317496162615
nan
0.44597911834716797
-119.65403220460225 37.736839161863564
nan
0.44397902488708496
-119.65403220460225 37.74236067629751
nan
0.4377310276031494
-119.65403220460225 37.74788203948328
nan
0.44394397735595703
-119.65403220460225 37.75340325143948
nan
0.44364023208618164
-119.65403220460225 37.758924312184746
nan
0.4352610111236572
-119.65403220460225 37.764445221737844
nan
0.4355752468109131
-119.65403220460225 37.76996598011727
nan
0.4410731792449951
-119.65503220460224 37.776486587341815
nan
0.43753

nan
0.4973759651184082
-119.64557957250985 37.75340325143948
nan
0.4927518367767334
-119.64557957250985 37.758924312184746
nan
0.48772120475769043
-119.64557957250985 37.764445221737844
nan
0.47945594787597656
-119.64557957250985 37.76996598011727
nan
0.4935288429260254
-119.64557957250985 37.77548658734182
nan
0.48230719566345215
-119.64557957250985 37.781007043430016
nan
0.48672008514404297
-119.64557957250985 37.78652734840053
nan
0.4539949893951416
-119.64557957250985 37.792047502272055
nan
0.4532630443572998
-119.64557957250985 37.79756750506312
nan
0.47038912773132324
-119.64557957250985 37.80308735679241
nan
0.4578278064727783
-119.64557957250985 37.808607057478454
nan
0.4542222023010254
-119.64557957250985 37.814126607140004
nan
0.4483070373535156
-119.64557957250985 37.81964600579557
nan
0.4489631652832031
-119.64557957250985 37.82516525346369
nan
0.454052209854126
-119.64557957250985 37.83068435016305
nan
0.4615051746368408
-119.64557957250985 37.836203295912206
nan
0.4514470

In [22]:
def main():       
    lanzarFuncionYosemite(x=-119.9, y=37.75, fecha='2019-02-22' ,tamanyoLadoMapaMetros=30000,PrecisionX10KmDeLado=60)

if __name__ == "__main__":
    main()

Se recoge un punto cada 500.0 metros
EL MAPA SE BASARA EN 3721 PUNTOS DE INFORMACION

Las esquinas del mapa son:
((-120.02342075916151, 37.58700334625748), (-120.02342075916151, 37.91286528855048), (-119.77182278123487, 37.59253081278702), (-119.77182278123487, 37.918383849495555))
HAY QUE CREAR LOS DATOS TOPOGRAFICOS


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/pandas/core/groupby/ops.py:958: FutureWarning:     You are passing non-geometry data to the GeoSeries constructor. Currently,
    it falls back to returning a pandas Series. But in the future, we will start
    to raise a TypeError instead.
  return type(sdata)(mgr, name=sdata.name, fastpath=True)


0 de 3721


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/pandas/core/groupby/ops.py:958: FutureWarning:     You are passing non-geometry data to the GeoSeries constructor. Currently,
    it falls back to returning a pandas Series. But in the future, we will start
    to raise a TypeError instead.
  return type(sdata)(mgr, name=sdata.name, fastpath=True)


4.9241859912872314
1 de 3721


...

0.27525807940955965
0.4474952220916748
-119.80549956036752 37.62569243138487
0.27479838533547507
0.4670381546020508
-119.80549956036752 37.63121883789778
0.2743024541539591
0.4594101905822754
-119.80549956036752 37.636745093055254
nan
0.447857141494751
-119.80549956036752 37.642271196876216
nan
0.47087979316711426
-119.80549956036752 37.647797149379585
nan
0.4782731533050537
-119.80549956036752 37.65332295058422
nan
0.45897483825683594
-119.80549956036752 37.658848600508925
nan
0.45154786109924316
-119.80549956036752 37.66437409917255
nan
0.46029210090637207
-119.80549956036752 37.669899446594044
nan
0.4585390090942383
-119.80549956036752 37.67542464279217
nan
0.44933199882507324
-119.80549956036752 37.680949687785805
nan
0.4460151195526123
-119.80549956036752 37.68647458159376
nan
0.44797301292419434
-119.80549956036752 37.69199932423481
nan
0.4504668712615967
-119.80549956036752 37.69752391572787
nan
0.4734048843383789
-119.80549956036752 37.70304835609175
nan
0.4545600414276123
-119

nan
0.4405388832092285
-119.79708414001203 37.67542464279217
nan
0.46852779388427734
-119.79708414001203 37.680949687785805
nan
0.45400285720825195
-119.79708414001203 37.68647458159376
nan
0.4551069736480713
-119.79708414001203 37.69199932423481
nan
0.464763879776001
-119.79708414001203 37.69752391572787
nan
0.4532032012939453
-119.79708414001203 37.70304835609175
nan
0.4441039562225342
-119.79708414001203 37.708572645345214
nan
0.4414689540863037
-119.79708414001203 37.714096783507124
nan
0.4760010242462158
-119.79708414001203 37.71962077059624
nan
0.4570329189300537
-119.79708414001203 37.72514460663137
nan
0.4632840156555176
-119.79708414001203 37.730668291631304
nan
0.46382832527160645
-119.79708414001203 37.736191825614796
nan
0.47626590728759766
-119.79708414001203 37.741715208600695
nan
0.45150327682495117
-119.79708414001203 37.74723844060769
nan
0.4684619903564453
-119.79708414001203 37.75276152165466
nan
0.45911192893981934
-119.79708414001203 37.75828445176026
nan
0.4545879

nan
0.463759183883667
-119.78866620403551 37.736191825614796
nan
0.4607820510864258
-119.78866620403551 37.741715208600695
nan
0.465850830078125
-119.78866620403551 37.74723844060769
nan
0.4671359062194824
-119.78866620403551 37.75276152165466
nan
0.4844789505004883
-119.78866620403551 37.75828445176026
nan
0.45732784271240234
-119.78866620403551 37.763807230943314
nan
0.4875771999359131
-119.78866620403551 37.76932985922257
nan
0.47371602058410645
-119.78866620403551 37.774852336616746
nan
0.4709510803222656
-119.78866620403551 37.78037466314456
nan
0.44447779655456543
-119.78866620403551 37.78589683882482
nan
0.4471890926361084
-119.78866620403551 37.79141886367621
nan
0.465407133102417
-119.78866620403551 37.79694073771752
nan
0.45618605613708496
-119.78866620403551 37.80246246096739
nan
0.45620203018188477
-119.78866620403551 37.80798403344455
nan
0.4773259162902832
-119.78866620403551 37.81350545516775
nan
0.47445201873779297
-119.78866620403551 37.81902672615565
nan
0.46514987945

nan
0.4532339572906494
-119.78024575144192 37.79694073771752
nan
0.4360067844390869
-119.78024575144192 37.80246246096739
nan
0.4443778991699219
-119.78024575144192 37.80798403344455
nan
0.4366767406463623
-119.78024575144192 37.81350545516775
nan
0.43909406661987305
-119.78024575144192 37.81902672615565
nan
0.4367790222167969
-119.78024575144192 37.824547846427
nan
0.4664900302886963
-119.78024575144192 37.83006881600043
nan
0.4612240791320801
-119.78024575144192 37.83558963489472
nan
0.46517515182495117
-119.78024575144192 37.84111030312842
nan
0.4620332717895508
-119.78024575144192 37.846630820720314
nan
0.46292805671691895
-119.78024575144192 37.85215118768903
nan
0.44278907775878906
-119.78024575144192 37.857671404053214
nan
0.4457690715789795
-119.78024575144192 37.8631914698316
nan
0.4326331615447998
-119.78024575144192 37.86871138504281
nan
0.43695497512817383
-119.78024575144192 37.87423114970545
nan
0.43702197074890137
-119.78024575144192 37.879750763838224
nan
0.443213939666

nan
0.47540998458862305
-119.77182278123487 37.857671404053214
nan
0.4802849292755127
-119.77182278123487 37.8631914698316
nan
0.475816011428833
-119.77182278123487 37.86871138504281
nan
0.47126078605651855
-119.77182278123487 37.87423114970545
nan
0.4756338596343994
-119.77182278123487 37.879750763838224
nan
0.46733999252319336
-119.77182278123487 37.88527022745973
nan
0.4726722240447998
-119.77182278123487 37.89078954058863
nan
0.4776911735534668
-119.77182278123487 37.89630870324349
nan
0.47057104110717773
-119.77182278123487 37.901827715443034
nan
0.48198390007019043
-119.77182278123487 37.9073465772058
nan
0.48104286193847656
-119.77282278123488 37.913865288550475
nan
0.4843881130218506
-119.77182278123487 37.918383849495555
nan
0.49245500564575195
(3721, 8, 25, 25)
Se han eliminado 29768 NANs
(3721, 8, 25, 25)
            long        lat               datos      meteo MATRIZ_FINAL  \
0    -120.023421  37.587003           Con datos  Con datos    CON DATOS   
1    -120.023421  37.5

In [23]:
def main():       
    lanzarFuncionYosemite(x=-119.9, y=37.75, fecha='2014-07-22' ,tamanyoLadoMapaMetros=30000,PrecisionX10KmDeLado=60)

if __name__ == "__main__":
    main()

Se recoge un punto cada 500.0 metros
EL MAPA SE BASARA EN 3721 PUNTOS DE INFORMACION

Las esquinas del mapa son:
((-120.02342075916151, 37.58700334625748), (-120.02342075916151, 37.91286528855048), (-119.77182278123487, 37.59253081278702), (-119.77182278123487, 37.918383849495555))
matrices de datos topograficos YA CREADOS ANTERIORMENTE
df de datos topograficos tb Cargados
-120.02342075916151 37.587003346257475
0.24632570178916385
0.5443079471588135
-120.02342075916151 37.592530812787025
0.24452570177704253
0.46706509590148926
-120.02342075916151 37.59805812782886
0.24276731775790897
0.47403788566589355
-120.02342075916151 37.60358529140193
0.24051166363785992
0.4626193046569824
-120.02342075916151 37.60911230352522
0.23940065712384112
0.4688539505004883
-120.02342075916151 37.61463916421749
0.23875080878561453
0.4466128349304199
-120.02342075916151 37.62016587349782
0.2381331049793286
0.4368300437927246
-120.02342075916151 37.62569243138487
0.23753053307215113
0.47887516021728516
-120

0.23673911888055804
0.4325718879699707
-120.01924588914677 37.81350545516775
0.23809122803244728
0.4384000301361084
-120.01924588914677 37.81902672615565
0.23932386866596983
0.4330408573150635
-120.01924588914677 37.824547846427
0.2395760295356983
0.439788818359375
-120.01924588914677 37.83006881600043
0.23800544355192146
0.4356989860534668
-120.01924588914677 37.83558963489472
0.23629325905618498
0.4401841163635254
-120.01924588914677 37.841110303128424
0.23495576691233389
0.4369351863861084
-120.01924588914677 37.84663082072032
0.23337204030056452
0.4485630989074707
-120.01924588914677 37.85215118768903
0.2324431700059251
0.434643030166626
-120.01924588914677 37.85767140405322
0.23183561855747767
0.4333000183105469
-120.01924588914677 37.8631914698316
0.23136754461166478
0.4335789680480957
-120.01924588914677 37.86871138504281
0.23066440615813502
0.4360840320587158
-120.01924588914677 37.87423114970545
0.2302903350772816
0.4403979778289795
-120.01924588914677 37.879750763838224
0.230

0.23307083666364617
0.4689028263092041
-120.01089428195492 37.736191825614796
0.23333239580819898
0.46175384521484375
-120.01089428195492 37.741715208600695
0.23371863458099484
0.4723532199859619
-120.01089428195492 37.74723844060769
0.2334831993988071
0.4485011100769043
-120.01089428195492 37.752761521654655
0.23307713797655752
0.47162699699401855
-120.01089428195492 37.75828445176026
0.23307566370690241
0.4499530792236328
-120.01089428195492 37.763807230943314
0.23267985740593117
0.4523341655731201
-120.01089428195492 37.769329859222566
0.2325332649084705
0.44797706604003906
-120.01089428195492 37.77485233661674
0.23344618820755605
0.436647891998291
-120.01189428195492 37.78137466314457
0.23432687990686568
0.456071138381958
-120.01089428195492 37.78589683882482
0.23505579016146522
0.4611349105834961
-120.01089428195492 37.791418863676206
0.23585107052891993
0.45067691802978516
-120.01089428195492 37.79694073771752
0.2367855626759244
0.4465467929840088
-120.01089428195492 37.802462460

0.23785274412301866
0.4451289176940918
-120.00254018439274 37.64779714937959
0.2386145193058208
0.44022679328918457
-120.00254018439274 37.65332295058422
0.2393843998980922
0.44078803062438965
-120.00254018439274 37.658848600508925
0.24004158623466643
0.43854427337646484
-120.00254018439274 37.66437409917255
0.24011177071619497
0.4382750988006592
-120.00254018439274 37.669899446594044
0.23916856151969212
0.43947911262512207
-120.00254018439274 37.67542464279217
0.23837951439994146
0.44007277488708496
-120.00254018439274 37.68094968778581
0.23744701461962545
0.4535207748413086
-120.00254018439274 37.68647458159376
0.23647594986798504
0.4425621032714844
-120.00254018439274 37.691999324234814
0.23570207791530884
0.4406912326812744
-120.00254018439274 37.69752391572787
0.23492356332535033
0.4548768997192383
-120.00254018439274 37.70304835609175
0.2341519688775331
0.4630148410797119
-120.00254018439274 37.70857264534522
0.2334430464668629
0.4618401527404785
-120.00254018439274 37.7140967835

/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:85: UserWarning: Warning: converting a masked element to nan.
/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:214: RuntimeWarning: invalid value encountered in true_divide


...

0.2392065480344196
0.4591200351715088
-119.80549956036751 37.61463916421749
0.23911483256500132
0.46859002113342285
-119.80549956036751 37.62016587349782
0.239050771689942
0.4645519256591797
-119.80549956036751 37.62569243138487
0.23906188335497505
0.45221614837646484
-119.80549956036751 37.631218837897784
0.2389076411533555
0.4689619541168213
-119.80549956036751 37.63674509305525
nan
0.45782470703125
-119.80549956036751 37.64227119687622
nan
0.4747507572174072
-119.80549956036751 37.64779714937959
nan
0.4728219509124756
-119.80549956036751 37.65332295058422
nan
0.47843003273010254
-119.80549956036751 37.658848600508925
nan
0.4603140354156494
-119.80549956036751 37.66437409917255
nan
0.4689829349517822
-119.80549956036751 37.669899446594044
nan
0.4703061580657959
-119.80549956036751 37.67542464279217
nan
0.4601132869720459
-119.80549956036751 37.68094968778581
nan
0.4578399658203125
-119.80549956036751 37.68647458159376
nan
0.4631359577178955
-119.80549956036751 37.691999324234814
nan


nan
0.4732992649078369
-119.79708414001206 37.658848600508925
nan
0.4671931266784668
-119.79708414001206 37.66437409917255
nan
0.4686000347137451
-119.79708414001206 37.669899446594044
nan
0.4754328727722168
-119.79708414001206 37.67542464279217
nan
0.4672119617462158
-119.79708414001206 37.68094968778581
nan
0.4642140865325928
-119.79708414001206 37.68647458159376
nan
0.4409022331237793
-119.79708414001206 37.691999324234814
nan
0.440122127532959
-119.79708414001206 37.69752391572787
nan
0.44296908378601074
-119.79708414001206 37.70304835609175
nan
0.44284582138061523
-119.79708414001206 37.70857264534522
nan
0.4410362243652344
-119.79708414001206 37.71409678350712
nan
0.44110703468322754
-119.79708414001206 37.719620770596244
nan
0.4388692378997803
-119.79708414001206 37.72514460663137
nan
0.45110607147216797
-119.79708414001206 37.7306682916313
nan
0.4384310245513916
-119.79708414001206 37.736191825614796
nan
0.4507427215576172
-119.79708414001206 37.741715208600695
nan
0.4427170753

nan
0.44266319274902344
-119.78866620403551 37.72514460663137
nan
0.4400608539581299
-119.78866620403551 37.7306682916313
nan
0.4560091495513916
-119.78866620403551 37.736191825614796
nan
0.4401090145111084
-119.78866620403551 37.741715208600695
nan
0.44199490547180176
-119.78866620403551 37.74723844060769
nan
0.44004130363464355
-119.78866620403551 37.752761521654655
nan
0.44600796699523926
-119.78866620403551 37.75828445176026
nan
0.44065308570861816
-119.78866620403551 37.763807230943314
nan
0.43952512741088867
-119.78866620403551 37.769329859222566
nan
0.4409968852996826
-119.78866620403551 37.77485233661674
nan
0.43765878677368164
-119.78866620403551 37.78037466314456
nan
0.44527196884155273
-119.78866620403551 37.78589683882482
nan
0.4425501823425293
-119.78866620403551 37.791418863676206
nan
0.43937206268310547
-119.78866620403551 37.79694073771752
nan
0.4394509792327881
-119.78866620403551 37.80246246096739
nan
0.45090508460998535
-119.78866620403551 37.80798403344455
nan
0.438

nan
0.43772196769714355
-119.78024575144191 37.791418863676206
nan
0.437697172164917
-119.78024575144191 37.79694073771752
nan
0.44034600257873535
-119.78024575144191 37.80246246096739
nan
0.4392571449279785
-119.78024575144191 37.80798403344455
nan
0.4394857883453369
-119.78024575144191 37.81350545516775
nan
0.4471890926361084
-119.78024575144191 37.81902672615565
nan
0.4368550777435303
-119.78024575144191 37.824547846427
nan
0.43788814544677734
-119.78024575144191 37.83006881600043
nan
0.43627071380615234
-119.78024575144191 37.83558963489472
nan
0.4387509822845459
-119.78024575144191 37.841110303128424
nan
0.44130587577819824
-119.78024575144191 37.84663082072032
nan
0.4441802501678467
-119.78024575144191 37.85215118768903
nan
0.4394710063934326
-119.78024575144191 37.85767140405322
nan
0.43934011459350586
-119.78024575144191 37.8631914698316
nan
0.439619779586792
-119.78024575144191 37.86871138504281
nan
0.4394948482513428
-119.78024575144191 37.87423114970545
nan
0.440365076065063

nan
0.47106194496154785
-119.77182278123487 37.85767140405322
nan
0.4691801071166992
-119.77182278123487 37.8631914698316
nan
0.4561879634857178
-119.77182278123487 37.86871138504281
nan
0.45940399169921875
-119.77182278123487 37.87423114970545
nan
0.4592130184173584
-119.77182278123487 37.879750763838224
nan
0.46703600883483887
-119.77182278123487 37.88527022745973
nan
0.4639859199523926
-119.77182278123487 37.890789540588635
nan
0.4645509719848633
-119.77182278123487 37.89630870324349
nan
0.4438316822052002
-119.77182278123487 37.90182771544304
nan
0.4469411373138428
-119.77182278123487 37.90734657720579
nan
0.47895288467407227
-119.77282278123488 37.913865288550475
nan
0.46509385108947754
-119.77182278123487 37.91838384949556
nan
0.4757859706878662
(3721, 8, 25, 25)
Se han eliminado 29768 NANs
(3721, 8, 25, 25)
            long        lat               datos      meteo MATRIZ_FINAL  \
0    -120.023421  37.587003           Con datos  Con datos    CON DATOS   
1    -120.023421  37.592

In [8]:
def main():       
    lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2014-07-22' ,tamanyoLadoMapaMetros=10000,PrecisionX10KmDeLado=2)

if __name__ == "__main__":
    main()

Se recoge un punto cada 5000.0 metros
EL MAPA SE BASARA EN 4 PUNTOS DE INFORMACION

Las esquinas del mapa son:
((-119.81135177284568, 37.795727520918334), (-119.81135177284568, 37.90425788931744), (-119.72858745457619, 37.795727520918334), (-119.72858745457619, 37.90425788931744))
HAY QUE CREAR LOS DATOS TOPOGRAFICOS


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/pandas/core/groupby/ops.py:958: FutureWarning:     You are passing non-geometry data to the GeoSeries constructor. Currently,
    it falls back to returning a pandas Series. But in the future, we will start
    to raise a TypeError instead.
  return type(sdata)(mgr, name=sdata.name, fastpath=True)


0 de 4


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/pandas/core/groupby/ops.py:958: FutureWarning:     You are passing non-geometry data to the GeoSeries constructor. Currently,
    it falls back to returning a pandas Series. But in the future, we will start
    to raise a TypeError instead.
  return type(sdata)(mgr, name=sdata.name, fastpath=True)


5.305927991867065
1 de 4


...

4.104464054107666
3 de 4


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/pandas/core/groupby/ops.py:958: FutureWarning:     You are passing non-geometry data to the GeoSeries constructor. Currently,
    it falls back to returning a pandas Series. But in the future, we will start
    to raise a TypeError instead.
  return type(sdata)(mgr, name=sdata.name, fastpath=True)


4.850142955780029
4.855338096618652
-119.81135177284568 37.795727520918334


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:85: UserWarning: Warning: converting a masked element to nan.
/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:214: RuntimeWarning: invalid value encountered in true_divide


nan
0.5476291179656982
-119.81135177284568 37.90425788931744
nan
0.4899871349334717
-119.72858745457619 37.795727520918334
nan
0.48197507858276367
-119.72858745457619 37.90425788931744
nan
0.4699220657348633
(4, 8, 25, 25)
Se han eliminado 32 NANs
(4, 8, 25, 25)
         long        lat      datos      meteo MATRIZ_FINAL  prediccion
0 -119.811352  37.795728  Con datos  Con datos    CON DATOS    0.986992
1 -119.811352  37.904258  Con datos  Con datos    CON DATOS    0.965242
2 -119.728587  37.795728  Con datos  Con datos    CON DATOS    0.945944
3 -119.728587  37.904258  Con datos  Con datos    CON DATOS    0.003404

Para calcular 4 puntos ha tardado 21.895841121673584

The chances of fire in all the area is 0.7253956231288612


In [ ]:
nombreCR_TOPOentreComillas=netcdfDELDIA[14:-3] + "EN"+str(x) + "_" + str(y) + "A" + str(tamanyoLadoMapaMetros/1000) + "kmXlado"+ str(PrecisionX10KmDeLado)+"puntosXkm_TOPOGRAFIA"  
###
nombreCR_TOPOentreComillas[]

In [32]:
x[8][7].shape

(25, 25)

In [37]:
x_base = np.array(x)
print(x_base.shape)
nas=0
for lista in range(len(x_base)):
        for matriz in range(8):
            where_are_NaNs = np.isnan(x_base[lista][matriz])
            x_base[lista][matriz][where_are_NaNs] = 0
            nas+=1

print(f'Se han eliminado {nas} NANs')
    

(9, 8)
Se han eliminado 72 NANs


In [22]:
 x_base = np.array(YOSEMITE25x25x8)
    
    print(x_base.shape)
    
    nas=0
    for lista in range(len(x_base)):
        for matriz in range(8):
            where_are_NaNs = np.isnan(x_base[lista][matriz])
            x_base[lista][matriz][where_are_NaNs] = 0
            nas+=1

    print(f'Se han eliminado {nas} NANs')
    
    
    
        #reordenamos los datos para que sean (400, 25, 25, 8)
    
    print(x_base.shape)
    
    x_base=x_base.transpose (0,2,3,1)

NameError: name 'x_base' is not defined

In [ ]:
def main():       
    lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2019-02-22' ,tamanyoLadoMapaMetros=300000,PrecisionX10KmDeLado= 6)

if __name__ == "__main__":
    main()

In [ ]:
def main():       
    lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2019-02-22' ,tamanyoLadoMapaMetros=10000,PrecisionX10KmDeLado= 20)

if __name__ == "__main__":
    main()

In [ ]:
datospoli=meteoAmatriz(datosEntrecomillas="nc/wrf_LT_d03_2010-11-13.nc")
datospoli

In [ ]:
datospoli=meteoAmatriz(datosEntrecomillas=netcdfDELDIA)

cordAmatrizRapido(-121.523590,41.771904,datospoli)

In [ ]:


direccion=('matricesTerreno/matricesYOSEx8.pkl')  
with open(direccion, 'rb') as f:
    YOSEMITE25x25x8=pickle.load(f)
    
    
direccion=('dfTERRENO/yosemitePROYECCION.csv')
dfYOSEMITE_TOTAL = pd.read_csv(direccion, index_col=0)
    
dfYOSEMITE_TOTAL_F=resultadoYproyeccion(YOSEMITE25x25x8,dfYOSEMITE_TOTAL)

In [ ]:
x,y=-119.641, 37.869
tamanyoLadoMapaMetros=30000
    #TOTAL DE PUNTOS POR LADO
PrecisionX10KmDeLado= 60   #maximo 2 POR KM: ej 10000-20 
netcdfDELDIA="nc/wrf_LT_d03_2010-11-13.nc"


titulo=netcdfDELDIA[14:-3] + "EN"+str(x) + "_" + str(y) + "A" + str(tamanyoLadoMapaMetros/1000) + "kmXlado"+ str(PrecisionX10KmDeLado)+"puntosXkm"
direccion=('DFlistoParaHeatMap/'+titulo+'.csv')
dfYOSEMITE_TOTAL.to_csv(direccion)

In [ ]:
#para el analisis
import pandas as pd
import pickle
import rasterio
from rasterio import plot

texto='yosemiteConPREDICCION'
direccion=('dfTERRENO/'+texto+'.csv')
dfwhiteWolf = pd.read_csv(direccion, index_col=0)
print(len(dfwhiteWolf))

direccion=('matricesTerreno/matricesYOSEx8.pkl')  
with open(direccion, 'rb') as f:
    whiteWolf=pickle.load(f)
print(len(whiteWolf))


# eliges el punto de la matriz (como linea desde la esquina superior iz a la inferior derecha)
punto=0
print(dfwhiteWolf[punto:punto+1])



atributos=['demTif','sloTif','aspTif','fueTif','v_LFM', 'v_U10', 'v_V10', 'v_MO1']
for x in range(8):
    print(atributos[x])
    plot.show(whiteWolf[punto][x])

In [ ]:
whiteWolf[0][6][0]

In [ ]:
for x in range(10):
    print(x)
    plot.show(whiteWolf[x][6],vmin=0.5,vmax=0.6)

In [59]:
  
    
# la funcion final!

def lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2014-07-22' ,tamanyoLadoMapaMetros=30000,PrecisionX10KmDeLado= 60):
    #maximo 2 puntos por quilometro: ej 10000-20 
    
    start = time.time()
        
    netcdfDELDIA="nc/wrf_LT_d03_"+fecha+".nc"

   

    dfPuntosYosemite, esquinasTif = creacionPuntosHeatMap(long=x,lat=y,tamanyoLadoMapaMetros=tamanyoLadoMapaMetros,precisionX10KmDeLado=PrecisionX10KmDeLado)

    #esta funcion crea los tifs que necesitamos para recorrer el terreno deseado todos los resultados de topografia en 
    #PERO PARA QUE FUNCIONA NECESITA LOS TIFS DE TODA CALIFORNIA QUE SON MUY PESADOS
    #EN ESTE CASO YA SE HAN RECORTADO LOS TIFS PARA EL ANALISIS DE 40KM DE LADO DE YOSEMITE,
    #LOS TIFS REPRESENTAN 40KM DE LADO + 7KM POR LADO DE BUFFER PARA LA CNN = 54KM DE LADO

    #se han considerado los valores estandart de climatologia (para cualquier punto) 
    #humedad en naturalez viva : v_LFM=[0,300]
    #dirección del viento : v_U10=[-20,+20]
    #velocidad del viento : v_V10=[-20,+20]    
    #humedad en naturalez muerta : v_MO1=[0,1]
    
    
    
    
    #como la informacion topografica no cambia, primero se comprueba si ya se han calculado (y se han guardado)estas entradas anteriormente 
    #si se ya esta guardada no hace faltar recalcularla, basta con calcular la metereologia que si que cambia.
    nombreCR_TOPOentreComillas=netcdfDELDIA[14:-3] + "EN"+str(x) + "_" + str(y) + "A" + str(tamanyoLadoMapaMetros/1000) + "kmXlado"+ str(PrecisionX10KmDeLado)+"puntosXkm_TOPOGRAFIA"  
###
    try:
        direccion=("matricesTerreno/"+nombreCR_TOPOentreComillas+".pkl")  
        with open(direccion, 'rb') as f:
            matrizTopo=pickle.load(f)
            print("matrices de datos topograficos YA CREADOS ANTERIORMENTE")
            
            
            direccion=('dfTERRENO/'+nombreCR_TOPOentreComillas+'.csv')
            df = pd.read_csv(direccion, index_col=0)
            print("df de datos topograficos tb Cargados")           
            
        
    except IOError:
        print("HAY QUE CREAR LOS DATOS TOPOGRAFICOS")
        #si no las hemos calculado antes las calculamos ahora
        
        #boundary has es una red creada especilamente para este programa, que cubre los puntos que incluyen los ncdf con los que contamos 
        boundary=gpd.read_file("poligonoMeteo/nc_shrinkboundary.shp")
        #se crean los shapefiles para la captura
        tifAnalisis(x, y, esquinasTif, boundary)


        #esta funcion lanza todo el proceso de recogida de datos TOPOGRAFICOS
        df,matrizTopo=guardarMatricesYdfTOPO(dfPuntosYosemite,boundary,nombreCR_TOPOentreComillas)
        #df,matrizTopo=guardarMatricesYdfTOPO(dfPuntosYosemite, boundary)

    
    
    #esta funcion lanza todo el proceso de recogida de datos METEOROLOGICOS
    dfYOSEMITE_TOTAL,matrizMeteo=matizMeteoYOSEMITE(df, netcdfDELDIA)

    #esta funcion junta las dos matrices
    YOSEMITE25x25x8,dfYOSEMITE_TOTAL2=matrizFINAL25x25x8(dfYOSEMITE_TOTAL,matrizTopo,matrizMeteo)
    len(YOSEMITE25x25x8),len(YOSEMITE25x25x8[0])

    #4. PASAMOS EL RESULTADO POR LA RED NEURONAL
    
    
    return YOSEMITE25x25x8,dfYOSEMITE_TOTAL2

    dfYOSEMITE_TOTAL_F=resultadoYproyeccion(YOSEMITE25x25x8,dfYOSEMITE_TOTAL2)
    
    
    print(dfYOSEMITE_TOTAL_F)
    
    titulo=netcdfDELDIA[14:-3] + "EN"+str(x) + "_" + str(y) + "A" + str(tamanyoLadoMapaMetros/1000) + "kmXlado"+ str(PrecisionX10KmDeLado)+"puntosXkmET"
    direccion=('DFlistoParaHeatMap/'+titulo+'.csv')
    dfYOSEMITE_TOTAL.to_csv(direccion)

    end = time.time()
    print(f'\nPara calcular {PrecisionX10KmDeLado*PrecisionX10KmDeLado} puntos ha tardado {end - start}') 
    #dataframeDeResultados

    print(f'\nThe chances of fire in all the area is {dfYOSEMITE_TOTAL_F.prediccion.mean()}')

    yosemite=[]
    for x in range(len(dfYOSEMITE_TOTAL_F)):
        yosemite.append(dfYOSEMITE_TOTAL_F['prediccion'][x])
    n=len(yosemite)
    ns = np.ceil(np.sqrt(n)).astype(int)
    whiteWolf = np.reshape(yosemite,(ns,ns))


    #guardamos
    direccion=('matricesTerreno/heatmapWhitWolf.pkl')  
    with open(direccion, 'wb') as f:
        pickle.dump(whiteWolf, f)

In [60]:
def main():       
    return lanzarFuncionYosemite(x=-119.77, y=37.85, fecha='2014-07-22' ,tamanyoLadoMapaMetros=10000,PrecisionX10KmDeLado=3)
    
if __name__ == "__main__":
    YOSEMITE25x25x8,dfYOSEMITE_TOTAL2=main()
len(x)

Se recoge un punto cada 3333.3333333333335 metros
EL MAPA SE BASARA EN 9 PUNTOS DE INFORMACION

Las esquinas del mapa son:
((-119.81135177284568, 37.795727520918334), (-119.81135177284568, 37.90425788931744), (-119.72858745457619, 37.795727520918334), (-119.72858745457619, 37.90425788931744))
matrices de datos topograficos YA CREADOS ANTERIORMENTE
df de datos topograficos tb Cargados
-119.81135177284568 37.795727520918334


/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:85: UserWarning: Warning: converting a masked element to nan.
/Users/xaf/opt/anaconda3/envs/december2020/lib/python3.7/site-packages/ipykernel_launcher.py:79: RuntimeWarning: invalid value encountered in true_divide


nan
0.4942598342895508
-119.81135177284568 37.84999999999997
nan
0.4893760681152344
-119.81135177284568 37.904257889317435
nan
0.48461103439331055
-119.77 37.795727520918334
nan
0.4924778938293457
-119.77 37.84999999999997
nan
0.49259495735168457
-119.77 37.904257889317435
nan
0.486422061920166
-119.7285874545762 37.795727520918334
nan
0.5044581890106201
-119.7285874545762 37.84999999999997
nan
0.5074501037597656
-119.7285874545762 37.904257889317435
nan
0.4823489189147949
dfYOSEMITE_TOTAL:9
topo:9
meteo:9


9

In [61]:


x_base = np.array(YOSEMITE25x25x8)
    
print(x_base.shape)
    
nas=0
for lista in range(len(x_base)):
    for matriz in range(8):
        where_are_NaNs = np.isnan(x_base[lista][matriz])
        print(len(where_are_NaNs))
        x_base[lista][matriz][where_are_NaNs] = 0
        nas+=1

print(f'Se han eliminado {nas} NANs')
    
    
    
        #reordenamos los datos para que sean (400, 25, 25, 8)
    
print(x_base.shape)

(9, 8)
25
25
25
27
25
25
25
25
25
25
25
27
25
25
25
25
25
25
25
27
25
25
25
25
25
25
25
27
25
25
25
25
25
25
25
27
25
25
25
25
25
25
25
27
25
25
25
25
25
25
25
27
25
25
25
25
25
25
25
27
25
25
25
25
25
25
25
27
25
25
25
25
Se han eliminado 72 NANs
(9, 8)


In [45]:
len(YOSEMITE25x25x8[0][0])

25

In [48]:
x_base2 = np.array(x_base[0][0])
x_base2.shape

(25, 25)

In [8]:
def resultadoYproyeccion(YOSEMITE25x25x8,dfYOSEMITE_TOTAL):
    #print(dfYOSEMITE_TOTAL)
    x_base = np.array(YOSEMITE25x25x8)
    
    print(x_base.shape)
    
    nas=0
    for lista in range(len(x_base)):
        for matriz in range(8):
            where_are_NaNs = np.isnan(x_base[lista][matriz])
            x_base[lista][matriz][where_are_NaNs] = 0
            nas+=1

    print(f'Se han eliminado {nas} NANs')
    
    
    
        #reordenamos los datos para que sean (400, 25, 25, 8)
    
    print(x_base.shape)
    
    
    
    
    
    
    #x_base=x_base.transpose (0,2,3,1)

    
    
    
    
    
    
    #cargamos el modelo ya entrenado
    reconstructed_model = keras.models.load_model("modelos/my_h5_modelMEJOR_PLUS_982.h5")


    
    # hacemos una prediccion y ordenamos los resultados
    pred = reconstructed_model.predict(x_base) 

    #CREAMOS LISTA CON LOS DATOS QUE TENEMOS TENIENDO EN CUENTA QUE PUEDE HABRER CASILLAS VACIAS.
    #print(pred)
    probabilidadIgnicion=[]
    for x in range(len(pred)):
        probabilidadIgnicion.append(pred[x][0])
    
    #print(probabilidadIgnicion)
    npred=0
    dfYOSEMITE_TOTAL['prediccion']=0.0
    for x in range(len(dfYOSEMITE_TOTAL)):

        if dfYOSEMITE_TOTAL['MATRIZ_FINAL'][x]=="CON DATOS":
            #print(npred,probabilidadIgnicion[npred])
            
            
            dfYOSEMITE_TOTAL.at[x,'prediccion']= probabilidadIgnicion[npred]
            npred+=1
    #print(dfYOSEMITE_TOTAL)
    
    #yosemite

    direccion=('dfTERRENO/yosemiteConPREDICCION.csv')
    dfYOSEMITE_TOTAL.to_csv(direccion)
    
    return dfYOSEMITE_TOTAL
    